In [1]:
import IPython
from IPython import display 
print("IPython version: {}". format(IPython.__version__))
import keras as k
from keras.callbacks import TensorBoard, ModelCheckpoint, EarlyStopping, Callback
from keras.layers import Dense, Dropout
from keras.models import Sequential, model_from_json
from keras.optimizers import SGD
from keras.utils.vis_utils import plot_model

import matplotlib 
print("matplotlib version: {}". format(matplotlib.__version__))
%matplotlib inline
import matplotlib.pyplot as plt

import numpy as np 
print("NumPy version: {}". format(np.__version__))


import os
import os.path

import pandas as pd
print("pandas version: {}". format(pd.__version__))

import random
from random import seed

import seaborn as sns
print("seaborn version: {}". format(sns.__version__))

from sklearn.preprocessing import StandardScaler, MinMaxScaler


import sys 
print("Python version: {}". format(sys.version))

import tensorflow as tf
print('TensorFlow: {}'.format(tf.__version__))

import warnings
warnings.filterwarnings('ignore')

from subprocess import check_output
print(check_output(["ls", "/home/willian/Keras_Litologia/arquivos_csv"]).decode("utf8"))

IPython version: 7.8.0


Using TensorFlow backend.


matplotlib version: 3.1.1
NumPy version: 1.16.5
pandas version: 0.25.1
seaborn version: 0.9.0
Python version: 3.7.4 (default, Aug 13 2019, 20:35:49) 
[GCC 7.3.0]
TensorFlow: 1.14.0
test.csv
train.csv



In [2]:
np.random.seed(7)

## Preprocessamento

In [3]:
def load_data():
    """
    Função para carregar o datasets pelo panda.
    Retun: a variável passa a ser um dataframe do pandas, podendo ter acesso aos métodos da lib.
        dftrain = treinamento
        dftest = teste
    """
    dftrain = pd.read_csv('/home/willian/Keras_Litologia/arquivos_csv/train.csv')
    dftest = pd.read_csv('/home/willian/Keras_Litologia/arquivos_csv/test.csv')
    return dftrain, dftest

In [4]:
def data_encode(data_frame, classificador):
    """
    Função para transformar a coluna do classificado em multiclassificadores *litologia de 1 a 7.
    data_frame: dicionário a ser recebido.
    classificador: nome da coluna do classificador.
    Return: Um novo data frame com as linhas de classificação transformada em colunas.        
    """
    data_frame = pd.get_dummies(data_frame, columns=[classificador])
    return data_frame

In [5]:
def variables_x_y(data_frame, cabecalho, n):
    """
    Função para transforma as variáveis de características e classificadores.
    n  = as colunas que fazem parte do classificador.
    y = classificador.
    x = características.
    return: um data_frame de características e outro de classificador do dataset.
    """
    x = data_frame[cabecalho[:n]]
    y = data_frame[cabecalho[n:]]
    return x, y

In [6]:
def transfer_array_np(data_frame, vtype):
    """
    Função para transformar o data_frame em array numpy [ matriz numpy]
    df = data_frame a ser transformado
    vtype = nome da variavel do tipo a ser transformada
    Return: matriz numpy do dataset.
    """
    np_data_frame = np.array(data_frame, dtype=vtype)
    return np_data_frame

In [7]:
def preprocessamento():
    dftrain, dftest = load_data()
    train = data_encode(dftrain, 'Litologia')
    test = data_encode(dftest, 'Litologia')
    train = train.drop(['Poço'], axis = 1)
    test = test.drop(['Poço'], axis = 1)
    cabecalho_list = list(train.columns.values)
    
    # n = - 7 representa primeira coluna do classificado.
    n = -7
    
    x_train, y_train = variables_x_y(train, cabecalho_list, n)
    x_test, y_test = variables_x_y(test, cabecalho_list, n)
    X_train = transfer_array_np(x_train, 'float32')
    y_train = transfer_array_np(y_train, 'int8')
    X_test = transfer_array_np(x_test, 'float32')
    y_test = transfer_array_np(y_test, 'int8')
    scaler = MinMaxScaler()
    x_train = scaler.fit_transform(X_train)
    x_test = scaler.fit_transform(X_test)
    return x_train, y_train, x_test, y_test

In [8]:
x_train, y_train, x_test, y_test = preprocessamento()

## ANN - Keras Modelo

In [9]:
def create_model(n_input, n_hidden, n_output, func_input, func_hidden, func_output):
    model = Sequential()
    model.add(Dense(n_input, input_dim = n_input, activation = func_input, kernel_initializer = 'uniform', bias_initializer = 'zeros'))
    model.add(Dense(n_hidden, activation = func_hidden))
    model.add(Dense(n_output, activation = func_output))
    opt = SGD(lr = 0.01, momentum = 0.9)
    model.compile(loss = 'categorical_crossentropy', optimizer = opt, metrics = ['acc', 'mse'])    
    print('Created to model.')
    return model

In [10]:
def load_model(path_file, num_model):
    json_file = open(path_file + 'model_' + num_model + '.json', 'r')
    loaded_model_json = json_file.read()
    json_file.close()
    model = model_from_json(loaded_model_json)
    print('Loaded model from disk')
    return model

In [11]:
epoch = 2500
batch_s = 10
path_file_models = '/home/willian/Keras_Litologia/model_save/Teste'

In [12]:
def verific_load_or_create(n_input, n_hidden, n_output, func_input, func_hidden, func_output, num_model):
    arquivo = True
    f_path = path_file_models + num_model + '/'
    file = f_path + 'model_' + num_model + '.json'
    if os.path.isfile(file) == True:
        model = load_model(path_file_models, num_model)
        return model, arquivo
    else:
        model = create_model(n_input, n_hidden, n_output, 'relu', 'relu', 'softmax')
        model.summary()
        #save_model(path_file_models, model16, '16')
        arquivo = False
        return model, arquivo 

In [13]:
def history_model(model, arquivo, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, num_model):
    if arquivo == False:
        checkpoint = [ModelCheckpoint(path_file_models + num_model + '/' + '{epoch:02d}_{acc:.2f}' + num_model + ".json", monitor='acc', verbose=1, save_best_only=True, save_weights_only=False, mode='max', period=1)]
        history = model.fit(x_train, y_train, validation_data = (x_test, y_test), callbacks=checkpoint, nb_epoch = epoch, verbose = 1, batch_size=batch_s, shuffle=True)
        score_train, score_test = score_model(model, x_train, y_train, x_test, y_test)
        return history, score_train, score_test
    else:
        opt = SGD(lr = 0.01, momentum = 0.9)
        history = model.compile(loss = 'categorical_crossentropy', optimizer = opt, metrics = ['acc', 'mse'])
        score_trapath_file_modelsin, score_test = score_model(model, x_train, y_train, x_test, y_test)
        return history, score_train, score_test 

In [14]:
def score_model(model, x_train, y_train, x_test, y_test):
    score_train = model.evaluate(x_train, y_train, verbose = 0)
    score_test = model.evaluate(x_test, y_test, verbose = 0)
    return score_train, score_test

In [15]:
def display_score(score_train, score_test):
    print(" Baseline Error Train: %.2f%%" % (100-score_train[1]*100))
    print(' Train Accuracy:', score_train[1])
    print(" Baseline Error Test: %.2f%%" % (100-score_test[1]*100))
    print(' Test Accuracy:', score_test[1])

### 1 - Camada Intermediária (Hidden-Layers) : quantidade de neurônio

#### Obs: Manipulação apenas da quantidade de neurônios na camada, demais parâmetros fixos.

#### 1.1 Teste da Camada Oculta (Hidden Layer) = 5

In [16]:
model11, arquivo11 = verific_load_or_create(20, 5, 7, 'relu', 'relu', 'softmax', '12')

W1112 10:26:38.603652 140448008505152 deprecation_wrapper.py:119] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W1112 10:26:38.639829 140448008505152 deprecation_wrapper.py:119] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W1112 10:26:38.643901 140448008505152 deprecation_wrapper.py:119] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W1112 10:26:38.803456 140448008505152 deprecation_wrapper.py:119] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/keras/optimizers.py:790: The name tf.train.Opt

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 20)                420       
_________________________________________________________________
dense_2 (Dense)              (None, 5)                 105       
_________________________________________________________________
dense_3 (Dense)              (None, 7)                 42        
Total params: 567
Trainable params: 567
Non-trainable params: 0
_________________________________________________________________


In [17]:
history11, score_train11, score_test11 = history_model(model11, arquivo11, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '11')

W1112 10:26:42.056008 140448008505152 deprecation.py:323] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/tensorflow/python/ops/math_grad.py:1250: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
W1112 10:26:42.147338 140448008505152 deprecation_wrapper.py:119] From /home/willian/.conda/envs/conda_tensorflow/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:986: The name tf.assign_add is deprecated. Please use tf.compat.v1.assign_add instead.



Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 2s 41ms/step - loss: 1.9426 - acc: 0.1957 - mean_squared_error: 0.1223 - val_loss: 1.9462 - val_acc: 0.1429 - val_mean_squared_error: 0.1225

Epoch 00001: acc improved from -inf to 0.19565, saving model to /home/willian/Keras_Litologia/model_save/Teste11/01_0.2011.json
Epoch 2/2500
46/46 [==============================] - 0s 511us/step - loss: 1.9251 - acc: 0.1957 - mean_squared_error: 0.1216 - val_loss: 1.9401 - val_acc: 0.1429 - val_mean_squared_error: 0.1222

Epoch 00002: acc did not improve from 0.19565
Epoch 3/2500
46/46 [==============================] - 0s 557us/step - loss: 1.9016 - acc: 0.1957 - mean_squared_error: 0.1207 - val_loss: 1.9329 - val_acc: 0.1429 - val_mean_squared_error: 0.1219

Epoch 00003: acc did not improve from 0.19565
Epoch 4/2500
46/46 [==============================] - 0s 727us/step - loss: 1.8798 - acc: 0.1957 - mean_squared_error: 0.1198 - val_loss: 1.9307 - 


Epoch 00028: acc improved from 0.56522 to 0.58696, saving model to /home/willian/Keras_Litologia/model_save/Teste11/28_0.5911.json
Epoch 29/2500
46/46 [==============================] - 0s 853us/step - loss: 1.1523 - acc: 0.5870 - mean_squared_error: 0.0868 - val_loss: 1.3925 - val_acc: 0.5714 - val_mean_squared_error: 0.0968

Epoch 00029: acc did not improve from 0.58696
Epoch 30/2500
46/46 [==============================] - 0s 844us/step - loss: 1.1197 - acc: 0.6087 - mean_squared_error: 0.0848 - val_loss: 1.3511 - val_acc: 0.5714 - val_mean_squared_error: 0.0933

Epoch 00030: acc improved from 0.58696 to 0.60870, saving model to /home/willian/Keras_Litologia/model_save/Teste11/30_0.6111.json
Epoch 31/2500
46/46 [==============================] - 0s 1ms/step - loss: 1.1051 - acc: 0.5652 - mean_squared_error: 0.0842 - val_loss: 1.3478 - val_acc: 0.7143 - val_mean_squared_error: 0.0921

Epoch 00031: acc did not improve from 0.60870
Epoch 32/2500
46/46 [==============================] 


Epoch 00059: acc did not improve from 0.67391
Epoch 60/2500
46/46 [==============================] - 0s 578us/step - loss: 0.7516 - acc: 0.6304 - mean_squared_error: 0.0612 - val_loss: 0.9240 - val_acc: 0.7143 - val_mean_squared_error: 0.0693

Epoch 00060: acc did not improve from 0.67391
Epoch 61/2500
46/46 [==============================] - 0s 883us/step - loss: 0.7408 - acc: 0.6957 - mean_squared_error: 0.0606 - val_loss: 1.0053 - val_acc: 0.5714 - val_mean_squared_error: 0.0766

Epoch 00061: acc improved from 0.67391 to 0.69565, saving model to /home/willian/Keras_Litologia/model_save/Teste11/61_0.7011.json
Epoch 62/2500
46/46 [==============================] - 0s 465us/step - loss: 0.7499 - acc: 0.6739 - mean_squared_error: 0.0610 - val_loss: 0.9808 - val_acc: 0.5714 - val_mean_squared_error: 0.0738

Epoch 00062: acc did not improve from 0.69565
Epoch 63/2500
46/46 [==============================] - 0s 458us/step - loss: 0.7072 - acc: 0.6522 - mean_squared_error: 0.0578 - val_los

46/46 [==============================] - 0s 598us/step - loss: 0.5334 - acc: 0.7826 - mean_squared_error: 0.0416 - val_loss: 0.6650 - val_acc: 0.8571 - val_mean_squared_error: 0.0459

Epoch 00090: acc did not improve from 0.82609
Epoch 91/2500
46/46 [==============================] - 0s 701us/step - loss: 0.5141 - acc: 0.8261 - mean_squared_error: 0.0399 - val_loss: 0.7069 - val_acc: 0.7143 - val_mean_squared_error: 0.0531

Epoch 00091: acc did not improve from 0.82609
Epoch 92/2500
46/46 [==============================] - 0s 569us/step - loss: 0.5276 - acc: 0.8043 - mean_squared_error: 0.0415 - val_loss: 0.6556 - val_acc: 0.7143 - val_mean_squared_error: 0.0479

Epoch 00092: acc did not improve from 0.82609
Epoch 93/2500
46/46 [==============================] - 0s 553us/step - loss: 0.5380 - acc: 0.7826 - mean_squared_error: 0.0428 - val_loss: 0.6273 - val_acc: 0.8571 - val_mean_squared_error: 0.0405

Epoch 00093: acc did not improve from 0.82609
Epoch 94/2500
46/46 [=================

...


Epoch 02340: acc did not improve from 1.00000
Epoch 2341/2500
46/46 [==============================] - 0s 417us/step - loss: 0.0031 - acc: 1.0000 - mean_squared_error: 1.5370e-05 - val_loss: 2.5374 - val_acc: 0.7143 - val_mean_squared_error: 0.0652

Epoch 02341: acc did not improve from 1.00000
Epoch 2342/2500
46/46 [==============================] - 0s 335us/step - loss: 0.0029 - acc: 1.0000 - mean_squared_error: 1.3108e-05 - val_loss: 2.5213 - val_acc: 0.7143 - val_mean_squared_error: 0.0635

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 383us/step - loss: 0.0030 - acc: 1.0000 - mean_squared_error: 1.4341e-05 - val_loss: 2.5131 - val_acc: 0.7143 - val_mean_squared_error: 0.0626

Epoch 02343: acc did not improve from 1.00000
Epoch 2344/2500
46/46 [==============================] - 0s 389us/step - loss: 0.0030 - acc: 1.0000 - mean_squared_error: 1.4703e-05 - val_loss: 2.5174 - val_acc: 0.7143 - val_mean_squared_error: 0.0631



Epoch 02373: acc did not improve from 1.00000
Epoch 2374/2500
46/46 [==============================] - 0s 429us/step - loss: 0.0030 - acc: 1.0000 - mean_squared_error: 1.4768e-05 - val_loss: 2.5211 - val_acc: 0.7143 - val_mean_squared_error: 0.0635

Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 355us/step - loss: 0.0028 - acc: 1.0000 - mean_squared_error: 1.2811e-05 - val_loss: 2.5389 - val_acc: 0.7143 - val_mean_squared_error: 0.0653

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 368us/step - loss: 0.0032 - acc: 1.0000 - mean_squared_error: 1.6474e-05 - val_loss: 2.5621 - val_acc: 0.7143 - val_mean_squared_error: 0.0675

Epoch 02376: acc did not improve from 1.00000
Epoch 2377/2500
46/46 [==============================] - 0s 376us/step - loss: 0.0029 - acc: 1.0000 - mean_squared_error: 1.3724e-05 - val_loss: 2.5484 - val_acc: 0.7143 - val_mean_squared_error: 0.0662



Epoch 02406: acc did not improve from 1.00000
Epoch 2407/2500
46/46 [==============================] - 0s 461us/step - loss: 0.0028 - acc: 1.0000 - mean_squared_error: 1.2306e-05 - val_loss: 2.5403 - val_acc: 0.7143 - val_mean_squared_error: 0.0654

Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 376us/step - loss: 0.0027 - acc: 1.0000 - mean_squared_error: 1.1960e-05 - val_loss: 2.5381 - val_acc: 0.7143 - val_mean_squared_error: 0.0652

Epoch 02408: acc did not improve from 1.00000
Epoch 2409/2500
46/46 [==============================] - 0s 368us/step - loss: 0.0028 - acc: 1.0000 - mean_squared_error: 1.2553e-05 - val_loss: 2.5310 - val_acc: 0.7143 - val_mean_squared_error: 0.0644

Epoch 02409: acc did not improve from 1.00000
Epoch 2410/2500
46/46 [==============================] - 0s 402us/step - loss: 0.0028 - acc: 1.0000 - mean_squared_error: 1.2498e-05 - val_loss: 2.5430 - val_acc: 0.7143 - val_mean_squared_error: 0.0656



Epoch 02439: acc did not improve from 1.00000
Epoch 2440/2500
46/46 [==============================] - 0s 394us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.1010e-05 - val_loss: 2.5426 - val_acc: 0.7143 - val_mean_squared_error: 0.0656

Epoch 02440: acc did not improve from 1.00000
Epoch 2441/2500
46/46 [==============================] - 0s 417us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.1095e-05 - val_loss: 2.5496 - val_acc: 0.7143 - val_mean_squared_error: 0.0663

Epoch 02441: acc did not improve from 1.00000
Epoch 2442/2500
46/46 [==============================] - 0s 424us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.1269e-05 - val_loss: 2.5493 - val_acc: 0.7143 - val_mean_squared_error: 0.0663

Epoch 02442: acc did not improve from 1.00000
Epoch 2443/2500
46/46 [==============================] - 0s 397us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.1126e-05 - val_loss: 2.5502 - val_acc: 0.7143 - val_mean_squared_error: 0.0663



Epoch 02472: acc did not improve from 1.00000
Epoch 2473/2500
46/46 [==============================] - 0s 438us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.0806e-05 - val_loss: 2.5527 - val_acc: 0.7143 - val_mean_squared_error: 0.0666

Epoch 02473: acc did not improve from 1.00000
Epoch 2474/2500
46/46 [==============================] - 0s 408us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.0926e-05 - val_loss: 2.5554 - val_acc: 0.7143 - val_mean_squared_error: 0.0668

Epoch 02474: acc did not improve from 1.00000
Epoch 2475/2500
46/46 [==============================] - 0s 373us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.0783e-05 - val_loss: 2.5483 - val_acc: 0.7143 - val_mean_squared_error: 0.0662

Epoch 02475: acc did not improve from 1.00000
Epoch 2476/2500
46/46 [==============================] - 0s 401us/step - loss: 0.0026 - acc: 1.0000 - mean_squared_error: 1.0611e-05 - val_loss: 2.5520 - val_acc: 0.7143 - val_mean_squared_error: 0.0665


In [18]:
display_score(score_train11, score_test11)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 28.57%
 Test Accuracy: 0.7142857313156128


In [19]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste11"]).decode("utf8"))

01_0.2011.json
05_0.2011.json
07_0.2211.json
08_0.2411.json
09_0.2611.json
10_0.2611.json
104_0.8511.json
12_0.2811.json
13_0.2811.json
14_0.3011.json
145_0.8911.json
15_0.3511.json
165_0.8911.json
20_0.3711.json
21_0.3911.json
212_0.9111.json
219_0.9311.json
22_0.4311.json
23_0.4811.json
232_0.9311.json
24_0.5011.json
25_0.5011.json
27_0.5711.json
28_0.5911.json
30_0.6111.json
32_0.6111.json
322_0.9311.json
34_0.6111.json
35_0.6511.json
40_0.6511.json
447_0.9611.json
455_0.9611.json
47_0.6711.json
50_0.6711.json
538_0.9811.json
607_0.9811.json
61_0.7011.json
65_0.7211.json
69_0.7411.json
70_0.7411.json
72_0.7411.json
75_0.7611.json
76_0.7811.json
80_0.8011.json
88_0.8311.json
889_1.0011.json



##### Época = 889 - Acc: 1.00

#### 1.2 Teste da Camada Oculta (Hidden Layer) = 10

In [20]:
model12, arquivo12 = verific_load_or_create(20, 10, 7, 'relu', 'relu', 'softmax', '12')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 20)                420       
_________________________________________________________________
dense_5 (Dense)              (None, 10)                210       
_________________________________________________________________
dense_6 (Dense)              (None, 7)                 77        
Total params: 707
Trainable params: 707
Non-trainable params: 0
_________________________________________________________________


In [21]:
history12, score_train12, score_test12 = history_model(model12, arquivo12, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '12')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 21ms/step - loss: 1.9482 - acc: 0.1957 - mean_squared_error: 0.1225 - val_loss: 1.9438 - val_acc: 0.1429 - val_mean_squared_error: 0.1224

Epoch 00001: acc improved from -inf to 0.19565, saving model to /home/willian/Keras_Litologia/model_save/Teste12/01_0.2012.json
Epoch 2/2500
46/46 [==============================] - 0s 1ms/step - loss: 1.9344 - acc: 0.2391 - mean_squared_error: 0.1220 - val_loss: 1.9379 - val_acc: 0.1429 - val_mean_squared_error: 0.1221

Epoch 00002: acc improved from 0.19565 to 0.23913, saving model to /home/willian/Keras_Litologia/model_save/Teste12/02_0.2412.json
Epoch 3/2500
46/46 [==============================] - 0s 978us/step - loss: 1.9163 - acc: 0.2391 - mean_squared_error: 0.1213 - val_loss: 1.9312 - val_acc: 0.2857 - val_mean_squared_error: 0.1218

Epoch 00003: acc did not improve from 0.23913
Epoch 4/2500
46/46 [==============================] - 0s 695us/s

46/46 [==============================] - 0s 746us/step - loss: 0.8567 - acc: 0.7174 - mean_squared_error: 0.0638 - val_loss: 1.0353 - val_acc: 0.7143 - val_mean_squared_error: 0.0723

Epoch 00030: acc improved from 0.67391 to 0.71739, saving model to /home/willian/Keras_Litologia/model_save/Teste12/30_0.7212.json
Epoch 31/2500
46/46 [==============================] - 0s 563us/step - loss: 0.8229 - acc: 0.7174 - mean_squared_error: 0.0616 - val_loss: 1.0245 - val_acc: 0.7143 - val_mean_squared_error: 0.0726

Epoch 00031: acc did not improve from 0.71739
Epoch 32/2500
46/46 [==============================] - 0s 833us/step - loss: 0.7990 - acc: 0.6957 - mean_squared_error: 0.0605 - val_loss: 1.0048 - val_acc: 0.7143 - val_mean_squared_error: 0.0722

Epoch 00032: acc did not improve from 0.71739
Epoch 33/2500
46/46 [==============================] - 0s 593us/step - loss: 0.7761 - acc: 0.7391 - mean_squared_error: 0.0589 - val_loss: 0.9623 - val_acc: 0.7143 - val_mean_squared_error: 0.0697



Epoch 00061: acc improved from 0.76087 to 0.80435, saving model to /home/willian/Keras_Litologia/model_save/Teste12/61_0.8012.json
Epoch 62/2500
46/46 [==============================] - 0s 414us/step - loss: 0.5093 - acc: 0.8043 - mean_squared_error: 0.0395 - val_loss: 0.4641 - val_acc: 0.8571 - val_mean_squared_error: 0.0387

Epoch 00062: acc improved from 0.80435 to 0.80435, saving model to /home/willian/Keras_Litologia/model_save/Teste12/62_0.8012.json
Epoch 63/2500
46/46 [==============================] - 0s 615us/step - loss: 0.4894 - acc: 0.8043 - mean_squared_error: 0.0384 - val_loss: 0.4558 - val_acc: 0.8571 - val_mean_squared_error: 0.0378

Epoch 00063: acc improved from 0.80435 to 0.80435, saving model to /home/willian/Keras_Litologia/model_save/Teste12/63_0.8012.json
Epoch 64/2500
46/46 [==============================] - 0s 909us/step - loss: 0.4581 - acc: 0.7609 - mean_squared_error: 0.0379 - val_loss: 0.5221 - val_acc: 0.7143 - val_mean_squared_error: 0.0437

Epoch 00064:

46/46 [==============================] - 0s 563us/step - loss: 0.4000 - acc: 0.8261 - mean_squared_error: 0.0328 - val_loss: 0.3309 - val_acc: 0.8571 - val_mean_squared_error: 0.0277

Epoch 00093: acc did not improve from 0.86957
Epoch 94/2500
46/46 [==============================] - 0s 535us/step - loss: 0.3859 - acc: 0.8478 - mean_squared_error: 0.0315 - val_loss: 0.2819 - val_acc: 1.0000 - val_mean_squared_error: 0.0207

Epoch 00094: acc did not improve from 0.86957
Epoch 95/2500
46/46 [==============================] - 0s 554us/step - loss: 0.3915 - acc: 0.8261 - mean_squared_error: 0.0318 - val_loss: 0.2850 - val_acc: 0.8571 - val_mean_squared_error: 0.0211

Epoch 00095: acc did not improve from 0.86957
Epoch 96/2500
46/46 [==============================] - 0s 660us/step - loss: 0.3854 - acc: 0.8478 - mean_squared_error: 0.0314 - val_loss: 0.3015 - val_acc: 0.8571 - val_mean_squared_error: 0.0240

Epoch 00096: acc did not improve from 0.86957
Epoch 97/2500
46/46 [=================


Epoch 00126: acc did not improve from 0.86957
Epoch 127/2500
46/46 [==============================] - 0s 476us/step - loss: 0.3460 - acc: 0.8478 - mean_squared_error: 0.0283 - val_loss: 0.2314 - val_acc: 1.0000 - val_mean_squared_error: 0.0170

Epoch 00127: acc did not improve from 0.86957
Epoch 128/2500
46/46 [==============================] - 0s 482us/step - loss: 0.3715 - acc: 0.8478 - mean_squared_error: 0.0316 - val_loss: 0.2634 - val_acc: 0.8571 - val_mean_squared_error: 0.0226

Epoch 00128: acc did not improve from 0.86957
Epoch 129/2500
46/46 [==============================] - 0s 469us/step - loss: 0.3348 - acc: 0.8261 - mean_squared_error: 0.0273 - val_loss: 0.2305 - val_acc: 0.8571 - val_mean_squared_error: 0.0183

Epoch 00129: acc did not improve from 0.86957
Epoch 130/2500
46/46 [==============================] - 0s 604us/step - loss: 0.3769 - acc: 0.7826 - mean_squared_error: 0.0323 - val_loss: 0.2183 - val_acc: 1.0000 - val_mean_squared_error: 0.0160

Epoch 00130: acc di

...


Epoch 02344: acc did not improve from 1.00000
Epoch 2345/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 4.5077e-06 - val_loss: 1.5554 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02345: acc did not improve from 1.00000
Epoch 2346/2500
46/46 [==============================] - 0s 802us/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 4.1548e-06 - val_loss: 1.5596 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02346: acc did not improve from 1.00000
Epoch 2347/2500
46/46 [==============================] - 0s 654us/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 4.0124e-06 - val_loss: 1.5586 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02347: acc did not improve from 1.00000
Epoch 2348/2500
46/46 [==============================] - 0s 824us/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 4.2972e-06 - val_loss: 1.5581 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

E


Epoch 02377: acc did not improve from 1.00000
Epoch 2378/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.3164e-06 - val_loss: 1.5691 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02378: acc did not improve from 1.00000
Epoch 2379/2500
46/46 [==============================] - 0s 610us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.7669e-06 - val_loss: 1.5659 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02379: acc did not improve from 1.00000
Epoch 2380/2500
46/46 [==============================] - 0s 767us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.7330e-06 - val_loss: 1.5636 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02380: acc did not improve from 1.00000
Epoch 2381/2500
46/46 [==============================] - 0s 700us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.9416e-06 - val_loss: 1.5619 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

E


Epoch 02410: acc did not improve from 1.00000
Epoch 2411/2500
46/46 [==============================] - 0s 428us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.8774e-06 - val_loss: 1.5728 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02411: acc did not improve from 1.00000
Epoch 2412/2500
46/46 [==============================] - 0s 496us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.8090e-06 - val_loss: 1.5729 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02412: acc did not improve from 1.00000
Epoch 2413/2500
46/46 [==============================] - 0s 856us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.4466e-06 - val_loss: 1.5766 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02413: acc did not improve from 1.00000
Epoch 2414/2500
46/46 [==============================] - 0s 824us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.7710e-06 - val_loss: 1.5761 - val_acc: 0.8571 - val_mean_squared_error: 0.0408



Epoch 02443: acc did not improve from 1.00000
Epoch 2444/2500
46/46 [==============================] - 0s 525us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.5938e-06 - val_loss: 1.5752 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02444: acc did not improve from 1.00000
Epoch 2445/2500
46/46 [==============================] - 0s 360us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.5161e-06 - val_loss: 1.5800 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02445: acc did not improve from 1.00000
Epoch 2446/2500
46/46 [==============================] - 0s 570us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.1331e-06 - val_loss: 1.5854 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02446: acc did not improve from 1.00000
Epoch 2447/2500
46/46 [==============================] - 0s 421us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.3696e-06 - val_loss: 1.5858 - val_acc: 0.8571 - val_mean_squared_error: 0.0408



Epoch 02476: acc did not improve from 1.00000
Epoch 2477/2500
46/46 [==============================] - 0s 464us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.0951e-06 - val_loss: 1.5887 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02477: acc did not improve from 1.00000
Epoch 2478/2500
46/46 [==============================] - 0s 528us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.2264e-06 - val_loss: 1.5897 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02478: acc did not improve from 1.00000
Epoch 2479/2500
46/46 [==============================] - 0s 478us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.2160e-06 - val_loss: 1.5894 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02479: acc did not improve from 1.00000
Epoch 2480/2500
46/46 [==============================] - 0s 670us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.5932e-06 - val_loss: 1.5847 - val_acc: 0.8571 - val_mean_squared_error: 0.0408


In [22]:
display_score(score_train12, score_test12)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [23]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste12"]).decode("utf8"))

01_0.2012.json
02_0.2412.json
04_0.3012.json
06_0.3012.json
07_0.3312.json
08_0.3912.json
11_0.4112.json
136_0.8912.json
148_0.9112.json
17_0.5012.json
18_0.5712.json
182_0.9112.json
20_0.5712.json
23_0.5912.json
234_0.9312.json
258_0.9312.json
26_0.6712.json
275_0.9612.json
30_0.7212.json
33_0.7412.json
34_0.7412.json
361_0.9612.json
379_0.9812.json
39_0.7612.json
429_1.0012.json
53_0.7612.json
57_0.7612.json
61_0.8012.json
62_0.8012.json
63_0.8012.json
73_0.8512.json
81_0.8512.json
91_0.8712.json



##### Época = 429 - Acc: 1.00

#### 1.3 Teste da Camada Oculta (Hidden Layer) = 15

In [25]:
model13, arquivo13 = verific_load_or_create(20, 15, 7, 'relu', 'relu', 'softmax', '13')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 20)                420       
_________________________________________________________________
dense_8 (Dense)              (None, 15)                315       
_________________________________________________________________
dense_9 (Dense)              (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [26]:
history13, score_train13, score_test13 = history_model(model13, arquivo13, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '13')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 15ms/step - loss: 1.9346 - acc: 0.3043 - mean_squared_error: 0.1220 - val_loss: 1.9466 - val_acc: 0.1429 - val_mean_squared_error: 0.1225

Epoch 00001: acc improved from -inf to 0.30435, saving model to /home/willian/Keras_Litologia/model_save/Teste13/01_0.3013.json
Epoch 2/2500
46/46 [==============================] - 0s 425us/step - loss: 1.9023 - acc: 0.2391 - mean_squared_error: 0.1206 - val_loss: 1.9519 - val_acc: 0.1429 - val_mean_squared_error: 0.1226

Epoch 00002: acc did not improve from 0.30435
Epoch 3/2500
46/46 [==============================] - 0s 478us/step - loss: 1.8699 - acc: 0.3043 - mean_squared_error: 0.1193 - val_loss: 1.9689 - val_acc: 0.1429 - val_mean_squared_error: 0.1231

Epoch 00003: acc improved from 0.30435 to 0.30435, saving model to /home/willian/Keras_Litologia/model_save/Teste13/03_0.3013.json
Epoch 4/2500
46/46 [==============================] - 0s 563us

46/46 [==============================] - 0s 612us/step - loss: 1.0607 - acc: 0.5652 - mean_squared_error: 0.0774 - val_loss: 1.4458 - val_acc: 0.2857 - val_mean_squared_error: 0.0971

Epoch 00031: acc did not improve from 0.58696
Epoch 32/2500
46/46 [==============================] - 0s 626us/step - loss: 1.0279 - acc: 0.5870 - mean_squared_error: 0.0751 - val_loss: 1.4554 - val_acc: 0.4286 - val_mean_squared_error: 0.0992

Epoch 00032: acc did not improve from 0.58696
Epoch 33/2500
46/46 [==============================] - 0s 833us/step - loss: 1.0199 - acc: 0.6087 - mean_squared_error: 0.0750 - val_loss: 1.4484 - val_acc: 0.4286 - val_mean_squared_error: 0.0998

Epoch 00033: acc improved from 0.58696 to 0.60870, saving model to /home/willian/Keras_Litologia/model_save/Teste13/33_0.6113.json
Epoch 34/2500
46/46 [==============================] - 0s 651us/step - loss: 1.0012 - acc: 0.5652 - mean_squared_error: 0.0742 - val_loss: 1.3906 - val_acc: 0.5714 - val_mean_squared_error: 0.0951


Epoch 62/2500
46/46 [==============================] - 0s 820us/step - loss: 0.5940 - acc: 0.7391 - mean_squared_error: 0.0472 - val_loss: 0.6279 - val_acc: 0.8571 - val_mean_squared_error: 0.0452

Epoch 00062: acc did not improve from 0.78261
Epoch 63/2500
46/46 [==============================] - 0s 603us/step - loss: 0.5866 - acc: 0.7609 - mean_squared_error: 0.0469 - val_loss: 0.6099 - val_acc: 0.7143 - val_mean_squared_error: 0.0468

Epoch 00063: acc did not improve from 0.78261
Epoch 64/2500
46/46 [==============================] - 0s 614us/step - loss: 0.5784 - acc: 0.7391 - mean_squared_error: 0.0468 - val_loss: 0.5901 - val_acc: 0.7143 - val_mean_squared_error: 0.0445

Epoch 00064: acc did not improve from 0.78261
Epoch 65/2500
46/46 [==============================] - 0s 633us/step - loss: 0.5704 - acc: 0.6739 - mean_squared_error: 0.0461 - val_loss: 0.6067 - val_acc: 0.8571 - val_mean_squared_error: 0.0443

Epoch 00065: acc did not improve from 0.78261
Epoch 66/2500
46/46 [===


Epoch 00094: acc did not improve from 0.84783
Epoch 95/2500
46/46 [==============================] - 0s 582us/step - loss: 0.4550 - acc: 0.7609 - mean_squared_error: 0.0398 - val_loss: 0.3123 - val_acc: 1.0000 - val_mean_squared_error: 0.0217

Epoch 00095: acc did not improve from 0.84783
Epoch 96/2500
46/46 [==============================] - 0s 990us/step - loss: 0.4384 - acc: 0.8261 - mean_squared_error: 0.0366 - val_loss: 0.3710 - val_acc: 0.8571 - val_mean_squared_error: 0.0307

Epoch 00096: acc did not improve from 0.84783
Epoch 97/2500
46/46 [==============================] - 0s 459us/step - loss: 0.4248 - acc: 0.8478 - mean_squared_error: 0.0352 - val_loss: 0.2889 - val_acc: 0.8571 - val_mean_squared_error: 0.0207

Epoch 00097: acc improved from 0.84783 to 0.84783, saving model to /home/willian/Keras_Litologia/model_save/Teste13/97_0.8513.json
Epoch 98/2500
46/46 [==============================] - 0s 546us/step - loss: 0.4588 - acc: 0.7391 - mean_squared_error: 0.0385 - val_los


Epoch 00127: acc did not improve from 0.86957
Epoch 128/2500
46/46 [==============================] - 0s 492us/step - loss: 0.3409 - acc: 0.8478 - mean_squared_error: 0.0283 - val_loss: 0.2418 - val_acc: 0.8571 - val_mean_squared_error: 0.0199

Epoch 00128: acc did not improve from 0.86957
Epoch 129/2500
46/46 [==============================] - 0s 436us/step - loss: 0.3453 - acc: 0.8478 - mean_squared_error: 0.0284 - val_loss: 0.2012 - val_acc: 0.8571 - val_mean_squared_error: 0.0139

Epoch 00129: acc did not improve from 0.86957
Epoch 130/2500
46/46 [==============================] - 0s 496us/step - loss: 0.3266 - acc: 0.8478 - mean_squared_error: 0.0266 - val_loss: 0.1831 - val_acc: 1.0000 - val_mean_squared_error: 0.0111

Epoch 00130: acc did not improve from 0.86957
Epoch 131/2500
46/46 [==============================] - 0s 946us/step - loss: 0.3564 - acc: 0.8478 - mean_squared_error: 0.0301 - val_loss: 0.1942 - val_acc: 1.0000 - val_mean_squared_error: 0.0118

Epoch 00131: acc di

...


Epoch 02345: acc did not improve from 1.00000
Epoch 2346/2500
46/46 [==============================] - 0s 579us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.8938e-06 - val_loss: 2.3092 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02346: acc did not improve from 1.00000
Epoch 2347/2500
46/46 [==============================] - 0s 581us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.7724e-06 - val_loss: 2.3094 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02347: acc did not improve from 1.00000
Epoch 2348/2500
46/46 [==============================] - 0s 448us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.7759e-06 - val_loss: 2.3093 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02348: acc did not improve from 1.00000
Epoch 2349/2500
46/46 [==============================] - 0s 773us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.7720e-06 - val_loss: 2.3091 - val_acc: 0.8571 - val_mean_squared_error: 0.0409



Epoch 02378: acc did not improve from 1.00000
Epoch 2379/2500
46/46 [==============================] - 0s 680us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.5056e-06 - val_loss: 2.3093 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02379: acc did not improve from 1.00000
Epoch 2380/2500
46/46 [==============================] - 0s 423us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.4975e-06 - val_loss: 2.3091 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02380: acc did not improve from 1.00000
Epoch 2381/2500
46/46 [==============================] - 0s 487us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.3175e-06 - val_loss: 2.3091 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02381: acc did not improve from 1.00000
Epoch 2382/2500
46/46 [==============================] - 0s 721us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.9423e-06 - val_loss: 2.3093 - val_acc: 0.8571 - val_mean_squared_error: 0.0409



Epoch 02411: acc did not improve from 1.00000
Epoch 2412/2500
46/46 [==============================] - 0s 935us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.4660e-06 - val_loss: 2.3091 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02412: acc did not improve from 1.00000
Epoch 2413/2500
46/46 [==============================] - 0s 354us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 3.0114e-06 - val_loss: 2.3094 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02413: acc did not improve from 1.00000
Epoch 2414/2500
46/46 [==============================] - 0s 457us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.8905e-06 - val_loss: 2.3095 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02414: acc did not improve from 1.00000
Epoch 2415/2500
46/46 [==============================] - 0s 285us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.4762e-06 - val_loss: 2.3095 - val_acc: 0.8571 - val_mean_squared_error: 0.0409



Epoch 02444: acc did not improve from 1.00000
Epoch 2445/2500
46/46 [==============================] - 0s 472us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.8325e-06 - val_loss: 2.3094 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02445: acc did not improve from 1.00000
Epoch 2446/2500
46/46 [==============================] - 0s 498us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.4836e-06 - val_loss: 2.3095 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02446: acc did not improve from 1.00000
Epoch 2447/2500
46/46 [==============================] - 0s 700us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.5607e-06 - val_loss: 2.3091 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02447: acc did not improve from 1.00000
Epoch 2448/2500
46/46 [==============================] - 0s 899us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.2277e-06 - val_loss: 2.3094 - val_acc: 0.8571 - val_mean_squared_error: 0.0409



Epoch 02477: acc did not improve from 1.00000
Epoch 2478/2500
46/46 [==============================] - 0s 645us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 3.1515e-06 - val_loss: 2.3095 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02478: acc did not improve from 1.00000
Epoch 2479/2500
46/46 [==============================] - 0s 545us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.4604e-06 - val_loss: 2.3093 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02479: acc did not improve from 1.00000
Epoch 2480/2500
46/46 [==============================] - 0s 574us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 3.0336e-06 - val_loss: 2.3092 - val_acc: 0.8571 - val_mean_squared_error: 0.0409

Epoch 02480: acc did not improve from 1.00000
Epoch 2481/2500
46/46 [==============================] - 0s 688us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.5541e-06 - val_loss: 2.3094 - val_acc: 0.8571 - val_mean_squared_error: 0.0409


In [27]:
display_score(score_train13, score_test13)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [28]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste13"]).decode("utf8"))

01_0.3013.json
03_0.3013.json
05_0.3313.json
06_0.3713.json
07_0.3913.json
08_0.5413.json
110_0.8713.json
144_0.9113.json
177_0.9113.json
197_0.9113.json
206_0.9313.json
212_0.9313.json
218_0.9613.json
219_0.9613.json
22_0.5413.json
237_0.9813.json
25_0.5713.json
26_0.5713.json
28_0.5913.json
306_1.0013.json
33_0.6113.json
36_0.6313.json
37_0.6513.json
38_0.6713.json
47_0.7213.json
53_0.7413.json
57_0.7613.json
61_0.7813.json
75_0.8013.json
77_0.8313.json
90_0.8513.json
97_0.8513.json



In [29]:
##### Época = 306 - Acc: 1.00

#### 1.4 Teste da Camada Oculta (Hidden Layer) = 20

In [30]:
model14, arquivo14 = verific_load_or_create(20, 20, 7, 'relu', 'relu', 'softmax', '14')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_10 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_11 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_12 (Dense)             (None, 7)                 147       
Total params: 987
Trainable params: 987
Non-trainable params: 0
_________________________________________________________________


In [31]:
history14, score_train14, score_test14 = history_model(model14, arquivo14, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '14')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 16ms/step - loss: 1.9378 - acc: 0.2174 - mean_squared_error: 0.1221 - val_loss: 1.9370 - val_acc: 0.1429 - val_mean_squared_error: 0.1221

Epoch 00001: acc improved from -inf to 0.21739, saving model to /home/willian/Keras_Litologia/model_save/Teste14/01_0.2214.json
Epoch 2/2500
46/46 [==============================] - 0s 358us/step - loss: 1.9022 - acc: 0.2609 - mean_squared_error: 0.1206 - val_loss: 1.9241 - val_acc: 0.1429 - val_mean_squared_error: 0.1215

Epoch 00002: acc improved from 0.21739 to 0.26087, saving model to /home/willian/Keras_Litologia/model_save/Teste14/02_0.2614.json
Epoch 3/2500
46/46 [==============================] - 0s 645us/step - loss: 1.8580 - acc: 0.2174 - mean_squared_error: 0.1188 - val_loss: 1.9171 - val_acc: 0.1429 - val_mean_squared_error: 0.1212

Epoch 00003: acc did not improve from 0.26087
Epoch 4/2500
46/46 [==============================] - 0s 553us

46/46 [==============================] - 0s 835us/step - loss: 0.8223 - acc: 0.6522 - mean_squared_error: 0.0637 - val_loss: 1.0016 - val_acc: 0.5714 - val_mean_squared_error: 0.0727

Epoch 00031: acc did not improve from 0.67391
Epoch 32/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.7872 - acc: 0.6304 - mean_squared_error: 0.0610 - val_loss: 1.0608 - val_acc: 0.5714 - val_mean_squared_error: 0.0790

Epoch 00032: acc did not improve from 0.67391
Epoch 33/2500
46/46 [==============================] - 0s 724us/step - loss: 0.7649 - acc: 0.6522 - mean_squared_error: 0.0603 - val_loss: 1.0074 - val_acc: 0.5714 - val_mean_squared_error: 0.0757

Epoch 00033: acc did not improve from 0.67391
Epoch 34/2500
46/46 [==============================] - 0s 794us/step - loss: 0.7427 - acc: 0.6957 - mean_squared_error: 0.0585 - val_loss: 0.9485 - val_acc: 0.5714 - val_mean_squared_error: 0.0733

Epoch 00034: acc improved from 0.67391 to 0.69565, saving model to /home/willian/Keras


Epoch 00062: acc improved from 0.80435 to 0.80435, saving model to /home/willian/Keras_Litologia/model_save/Teste14/62_0.8014.json
Epoch 63/2500
46/46 [==============================] - 0s 661us/step - loss: 0.4749 - acc: 0.7609 - mean_squared_error: 0.0378 - val_loss: 0.3647 - val_acc: 0.8571 - val_mean_squared_error: 0.0291

Epoch 00063: acc did not improve from 0.80435
Epoch 64/2500
46/46 [==============================] - 0s 575us/step - loss: 0.4670 - acc: 0.7826 - mean_squared_error: 0.0371 - val_loss: 0.3736 - val_acc: 0.8571 - val_mean_squared_error: 0.0294

Epoch 00064: acc did not improve from 0.80435
Epoch 65/2500
46/46 [==============================] - 0s 652us/step - loss: 0.4675 - acc: 0.7391 - mean_squared_error: 0.0374 - val_loss: 0.3247 - val_acc: 1.0000 - val_mean_squared_error: 0.0219

Epoch 00065: acc did not improve from 0.80435
Epoch 66/2500
46/46 [==============================] - 0s 546us/step - loss: 0.4682 - acc: 0.8043 - mean_squared_error: 0.0367 - val_los

46/46 [==============================] - 0s 761us/step - loss: 0.3962 - acc: 0.7826 - mean_squared_error: 0.0336 - val_loss: 0.2501 - val_acc: 0.8571 - val_mean_squared_error: 0.0207

Epoch 00095: acc did not improve from 0.84783
Epoch 96/2500
46/46 [==============================] - 0s 596us/step - loss: 0.3810 - acc: 0.8261 - mean_squared_error: 0.0299 - val_loss: 0.1986 - val_acc: 1.0000 - val_mean_squared_error: 0.0126

Epoch 00096: acc did not improve from 0.84783
Epoch 97/2500
46/46 [==============================] - 0s 647us/step - loss: 0.3804 - acc: 0.8043 - mean_squared_error: 0.0318 - val_loss: 0.2279 - val_acc: 1.0000 - val_mean_squared_error: 0.0155

Epoch 00097: acc did not improve from 0.84783
Epoch 98/2500
46/46 [==============================] - 0s 703us/step - loss: 0.4007 - acc: 0.8261 - mean_squared_error: 0.0332 - val_loss: 0.2406 - val_acc: 0.8571 - val_mean_squared_error: 0.0176

Epoch 00098: acc did not improve from 0.84783
Epoch 99/2500
46/46 [=================

46/46 [==============================] - 0s 759us/step - loss: 0.3451 - acc: 0.8696 - mean_squared_error: 0.0289 - val_loss: 0.1655 - val_acc: 1.0000 - val_mean_squared_error: 0.0097

Epoch 00128: acc did not improve from 0.89130
Epoch 129/2500
46/46 [==============================] - 0s 541us/step - loss: 0.3370 - acc: 0.8696 - mean_squared_error: 0.0273 - val_loss: 0.1823 - val_acc: 0.8571 - val_mean_squared_error: 0.0145

Epoch 00129: acc did not improve from 0.89130
Epoch 130/2500
46/46 [==============================] - 0s 711us/step - loss: 0.3746 - acc: 0.8478 - mean_squared_error: 0.0322 - val_loss: 0.2293 - val_acc: 0.8571 - val_mean_squared_error: 0.0210

Epoch 00130: acc did not improve from 0.89130
Epoch 131/2500
46/46 [==============================] - 0s 730us/step - loss: 0.3446 - acc: 0.8696 - mean_squared_error: 0.0286 - val_loss: 0.1535 - val_acc: 1.0000 - val_mean_squared_error: 0.0088

Epoch 00131: acc did not improve from 0.89130
Epoch 132/2500
46/46 [=============

...

46/46 [==============================] - 0s 478us/step - loss: 9.7056e-04 - acc: 1.0000 - mean_squared_error: 1.9253e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 904us/step - loss: 9.4104e-04 - acc: 1.0000 - mean_squared_error: 1.7870e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02343: acc did not improve from 1.00000
Epoch 2344/2500
46/46 [==============================] - 0s 511us/step - loss: 9.4101e-04 - acc: 1.0000 - mean_squared_error: 1.7826e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02344: acc did not improve from 1.00000
Epoch 2345/2500
46/46 [==============================] - 0s 389us/step - loss: 9.3853e-04 - acc: 1.0000 - mean_squared_error: 1.8004e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02345: acc did not improve from 1.00000


46/46 [==============================] - 0s 512us/step - loss: 9.3306e-04 - acc: 1.0000 - mean_squared_error: 1.8358e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 482us/step - loss: 9.2400e-04 - acc: 1.0000 - mean_squared_error: 1.7794e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 577us/step - loss: 9.2685e-04 - acc: 1.0000 - mean_squared_error: 1.7122e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02376: acc did not improve from 1.00000
Epoch 2377/2500
46/46 [==============================] - 0s 510us/step - loss: 9.3084e-04 - acc: 1.0000 - mean_squared_error: 1.7437e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02377: acc did not improve from 1.00000


46/46 [==============================] - 0s 536us/step - loss: 9.6622e-04 - acc: 1.0000 - mean_squared_error: 1.9754e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02406: acc did not improve from 1.00000
Epoch 2407/2500
46/46 [==============================] - 0s 1ms/step - loss: 9.1646e-04 - acc: 1.0000 - mean_squared_error: 1.7234e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 548us/step - loss: 9.0446e-04 - acc: 1.0000 - mean_squared_error: 1.6136e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02408: acc did not improve from 1.00000
Epoch 2409/2500
46/46 [==============================] - 0s 877us/step - loss: 8.9844e-04 - acc: 1.0000 - mean_squared_error: 1.6002e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02409: acc did not improve from 1.00000
Ep

46/46 [==============================] - 0s 449us/step - loss: 9.0965e-04 - acc: 1.0000 - mean_squared_error: 1.8665e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02438: acc did not improve from 1.00000
Epoch 2439/2500
46/46 [==============================] - 0s 546us/step - loss: 8.9724e-04 - acc: 1.0000 - mean_squared_error: 1.7844e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02439: acc did not improve from 1.00000
Epoch 2440/2500
46/46 [==============================] - 0s 508us/step - loss: 9.3373e-04 - acc: 1.0000 - mean_squared_error: 1.8573e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02440: acc did not improve from 1.00000
Epoch 2441/2500
46/46 [==============================] - 0s 483us/step - loss: 9.2496e-04 - acc: 1.0000 - mean_squared_error: 1.7503e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02441: acc did not improve from 1.00000


46/46 [==============================] - 0s 503us/step - loss: 8.5888e-04 - acc: 1.0000 - mean_squared_error: 1.4788e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02470: acc did not improve from 1.00000
Epoch 2471/2500
46/46 [==============================] - 0s 417us/step - loss: 8.8338e-04 - acc: 1.0000 - mean_squared_error: 1.5847e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02471: acc did not improve from 1.00000
Epoch 2472/2500
46/46 [==============================] - 0s 591us/step - loss: 9.2511e-04 - acc: 1.0000 - mean_squared_error: 1.8527e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02472: acc did not improve from 1.00000
Epoch 2473/2500
46/46 [==============================] - 0s 562us/step - loss: 8.9129e-04 - acc: 1.0000 - mean_squared_error: 1.6736e-06 - val_loss: 2.3028 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02473: acc did not improve from 1.00000


In [32]:
display_score(score_train14, score_test14)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [33]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste14"]).decode("utf8"))

01_0.2214.json
02_0.2614.json
07_0.3714.json
08_0.4614.json
09_0.5214.json
10_0.5414.json
109_0.8514.json
11_0.5914.json
113_0.8914.json
138_0.9114.json
139_0.9314.json
180_0.9314.json
18_0.6114.json
182_0.9314.json
223_0.9814.json
231_0.9814.json
24_0.6714.json
30_0.6714.json
34_0.7014.json
354_1.0014.json
40_0.7414.json
41_0.7614.json
56_0.7614.json
57_0.8014.json
61_0.8014.json
62_0.8014.json
79_0.8314.json
84_0.8314.json
93_0.8514.json



In [34]:
##### Época = 354 - Acc: 1.00

#### 1.5 Teste da Camada Oculta (Hidden Layer) = 27

In [39]:
model15, arquivo15 = verific_load_or_create(20, 27, 7, 'relu', 'relu', 'softmax', '15')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_16 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_17 (Dense)             (None, 27)                567       
_________________________________________________________________
dense_18 (Dense)             (None, 7)                 196       
Total params: 1,183
Trainable params: 1,183
Non-trainable params: 0
_________________________________________________________________


In [40]:
history15, score_train15, score_test15 = history_model(model15, arquivo15, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '15')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 29ms/step - loss: 1.9408 - acc: 0.2174 - mean_squared_error: 0.1222 - val_loss: 1.9333 - val_acc: 0.2857 - val_mean_squared_error: 0.1219

Epoch 00001: acc improved from -inf to 0.21739, saving model to /home/willian/Keras_Litologia/model_save/Teste15/01_0.2215.json
Epoch 2/2500
46/46 [==============================] - 0s 505us/step - loss: 1.9182 - acc: 0.3696 - mean_squared_error: 0.1213 - val_loss: 1.9181 - val_acc: 0.4286 - val_mean_squared_error: 0.1213

Epoch 00002: acc improved from 0.21739 to 0.36957, saving model to /home/willian/Keras_Litologia/model_save/Teste15/02_0.3715.json
Epoch 3/2500
46/46 [==============================] - 0s 865us/step - loss: 1.8888 - acc: 0.4565 - mean_squared_error: 0.1201 - val_loss: 1.8972 - val_acc: 0.4286 - val_mean_squared_error: 0.1204

Epoch 00003: acc improved from 0.36957 to 0.45652, saving model to /home/willian/Keras_Litologia/model_save/


Epoch 00030: acc did not improve from 0.65217
Epoch 31/2500
46/46 [==============================] - 0s 750us/step - loss: 0.8379 - acc: 0.6522 - mean_squared_error: 0.0639 - val_loss: 1.1241 - val_acc: 0.5714 - val_mean_squared_error: 0.0793

Epoch 00031: acc did not improve from 0.65217
Epoch 32/2500
46/46 [==============================] - 0s 919us/step - loss: 0.8316 - acc: 0.6522 - mean_squared_error: 0.0634 - val_loss: 1.0850 - val_acc: 0.5714 - val_mean_squared_error: 0.0780

Epoch 00032: acc did not improve from 0.65217
Epoch 33/2500
46/46 [==============================] - 0s 722us/step - loss: 0.8051 - acc: 0.6522 - mean_squared_error: 0.0612 - val_loss: 1.0192 - val_acc: 0.5714 - val_mean_squared_error: 0.0752

Epoch 00033: acc did not improve from 0.65217
Epoch 34/2500
46/46 [==============================] - 0s 807us/step - loss: 0.7946 - acc: 0.6522 - mean_squared_error: 0.0620 - val_loss: 0.9989 - val_acc: 0.5714 - val_mean_squared_error: 0.0766

Epoch 00034: acc did no


Epoch 00062: acc improved from 0.76087 to 0.78261, saving model to /home/willian/Keras_Litologia/model_save/Teste15/62_0.7815.json
Epoch 63/2500
46/46 [==============================] - 0s 655us/step - loss: 0.4760 - acc: 0.8261 - mean_squared_error: 0.0371 - val_loss: 0.4281 - val_acc: 0.7143 - val_mean_squared_error: 0.0339

Epoch 00063: acc improved from 0.78261 to 0.82609, saving model to /home/willian/Keras_Litologia/model_save/Teste15/63_0.8315.json
Epoch 64/2500
46/46 [==============================] - 0s 819us/step - loss: 0.4582 - acc: 0.8261 - mean_squared_error: 0.0353 - val_loss: 0.4341 - val_acc: 0.8571 - val_mean_squared_error: 0.0359

Epoch 00064: acc did not improve from 0.82609
Epoch 65/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.4853 - acc: 0.7174 - mean_squared_error: 0.0398 - val_loss: 0.4544 - val_acc: 0.7143 - val_mean_squared_error: 0.0398

Epoch 00065: acc did not improve from 0.82609
Epoch 66/2500
46/46 [==============================] 

46/46 [==============================] - 0s 490us/step - loss: 0.3886 - acc: 0.7826 - mean_squared_error: 0.0318 - val_loss: 0.3115 - val_acc: 0.8571 - val_mean_squared_error: 0.0248

Epoch 00095: acc did not improve from 0.86957
Epoch 96/2500
46/46 [==============================] - 0s 688us/step - loss: 0.3767 - acc: 0.8261 - mean_squared_error: 0.0306 - val_loss: 0.2707 - val_acc: 1.0000 - val_mean_squared_error: 0.0184

Epoch 00096: acc did not improve from 0.86957
Epoch 97/2500
46/46 [==============================] - 0s 550us/step - loss: 0.4051 - acc: 0.8043 - mean_squared_error: 0.0339 - val_loss: 0.3466 - val_acc: 0.8571 - val_mean_squared_error: 0.0286

Epoch 00097: acc did not improve from 0.86957
Epoch 98/2500
46/46 [==============================] - 0s 904us/step - loss: 0.3675 - acc: 0.7826 - mean_squared_error: 0.0305 - val_loss: 0.3140 - val_acc: 0.8571 - val_mean_squared_error: 0.0249

Epoch 00098: acc did not improve from 0.86957
Epoch 99/2500
46/46 [=================

Epoch 00127: acc did not improve from 0.89130
Epoch 128/2500
46/46 [==============================] - 0s 702us/step - loss: 0.3295 - acc: 0.8913 - mean_squared_error: 0.0269 - val_loss: 0.2945 - val_acc: 0.8571 - val_mean_squared_error: 0.0241

Epoch 00128: acc did not improve from 0.89130
Epoch 129/2500
46/46 [==============================] - 0s 823us/step - loss: 0.3226 - acc: 0.8478 - mean_squared_error: 0.0262 - val_loss: 0.2568 - val_acc: 0.8571 - val_mean_squared_error: 0.0197

Epoch 00129: acc did not improve from 0.89130
Epoch 130/2500
46/46 [==============================] - 0s 719us/step - loss: 0.3289 - acc: 0.8696 - mean_squared_error: 0.0272 - val_loss: 0.2510 - val_acc: 0.8571 - val_mean_squared_error: 0.0192

Epoch 00130: acc did not improve from 0.89130
Epoch 131/2500
46/46 [==============================] - 0s 780us/step - loss: 0.3136 - acc: 0.8696 - mean_squared_error: 0.0254 - val_loss: 0.2969 - val_acc: 0.8571 - val_mean_squared_error: 0.0247

Epoch 00131: acc did

...

46/46 [==============================] - 0s 890us/step - loss: 9.4313e-04 - acc: 1.0000 - mean_squared_error: 1.6226e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 851us/step - loss: 9.3401e-04 - acc: 1.0000 - mean_squared_error: 1.5759e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02343: acc did not improve from 1.00000
Epoch 2344/2500
46/46 [==============================] - 0s 614us/step - loss: 9.6009e-04 - acc: 1.0000 - mean_squared_error: 1.7038e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02344: acc did not improve from 1.00000
Epoch 2345/2500
46/46 [==============================] - 0s 857us/step - loss: 9.6941e-04 - acc: 1.0000 - mean_squared_error: 1.7996e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02345: acc did not improve from 1.00000


46/46 [==============================] - 0s 436us/step - loss: 9.4574e-04 - acc: 1.0000 - mean_squared_error: 1.7024e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 619us/step - loss: 9.2982e-04 - acc: 1.0000 - mean_squared_error: 1.6215e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 392us/step - loss: 9.1754e-04 - acc: 1.0000 - mean_squared_error: 1.5370e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02376: acc did not improve from 1.00000
Epoch 2377/2500
46/46 [==============================] - 0s 772us/step - loss: 9.2514e-04 - acc: 1.0000 - mean_squared_error: 1.5568e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02377: acc did not improve from 1.00000


46/46 [==============================] - 0s 453us/step - loss: 8.9444e-04 - acc: 1.0000 - mean_squared_error: 1.4454e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02406: acc did not improve from 1.00000
Epoch 2407/2500
46/46 [==============================] - 0s 751us/step - loss: 9.7720e-04 - acc: 1.0000 - mean_squared_error: 1.9176e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 776us/step - loss: 9.2894e-04 - acc: 1.0000 - mean_squared_error: 1.7072e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02408: acc did not improve from 1.00000
Epoch 2409/2500
46/46 [==============================] - 0s 1ms/step - loss: 9.0311e-04 - acc: 1.0000 - mean_squared_error: 1.5222e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02409: acc did not improve from 1.00000
Ep

46/46 [==============================] - 0s 394us/step - loss: 9.1452e-04 - acc: 1.0000 - mean_squared_error: 1.5736e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02438: acc did not improve from 1.00000
Epoch 2439/2500
46/46 [==============================] - 0s 1ms/step - loss: 9.3290e-04 - acc: 1.0000 - mean_squared_error: 1.8058e-06 - val_loss: 2.3041 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02439: acc did not improve from 1.00000
Epoch 2440/2500
46/46 [==============================] - 0s 938us/step - loss: 8.9593e-04 - acc: 1.0000 - mean_squared_error: 1.5212e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02440: acc did not improve from 1.00000
Epoch 2441/2500
46/46 [==============================] - 0s 1ms/step - loss: 9.1402e-04 - acc: 1.0000 - mean_squared_error: 1.6086e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02441: acc did not improve from 1.00000
Epoc

46/46 [==============================] - 0s 887us/step - loss: 8.8902e-04 - acc: 1.0000 - mean_squared_error: 1.5069e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02470: acc did not improve from 1.00000
Epoch 2471/2500
46/46 [==============================] - 0s 488us/step - loss: 8.8489e-04 - acc: 1.0000 - mean_squared_error: 1.4643e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02471: acc did not improve from 1.00000
Epoch 2472/2500
46/46 [==============================] - 0s 554us/step - loss: 8.8060e-04 - acc: 1.0000 - mean_squared_error: 1.4452e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02472: acc did not improve from 1.00000
Epoch 2473/2500
46/46 [==============================] - 0s 724us/step - loss: 8.6693e-04 - acc: 1.0000 - mean_squared_error: 1.3748e-06 - val_loss: 2.3040 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02473: acc did not improve from 1.00000


In [41]:
display_score(score_train15, score_test15)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [42]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste15"]).decode("utf8"))

01_0.2215.json
02_0.3715.json
03_0.4615.json
107_0.8915.json
123_0.8915.json
13_0.4815.json
137_0.9115.json
14_0.4815.json
160_0.9115.json
16_0.5015.json
162_0.9315.json
17_0.5915.json
189_0.9315.json
19_0.6315.json
196_0.9615.json
199_0.9615.json
22_0.6515.json
23_0.6515.json
24_0.6515.json
276_0.9815.json
335_1.0015.json
35_0.6715.json
41_0.7015.json
45_0.7215.json
46_0.7615.json
49_0.7615.json
62_0.7815.json
63_0.8315.json
79_0.8515.json
91_0.8715.json



##### Época = 335 - Acc: 1.00

### 2 - Camada Intermediária (Hidden-Layers) : função de ativação

##### Obs: O modelo que apresentou o melhor resultado foi o 1.3, com 15 neurônios na camada oculta, todos os teste foram realizados usando a função Relu na camada oculta. Os próximos teste serão realizados alterando a função de ativação da camada oculta.

#### 2.1 Teste da Camada Oculta (Hidden Layer) =  Função de Ativação 'Relu' ( 1.3 do teste anterior)

In [43]:
model13.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 20)                420       
_________________________________________________________________
dense_8 (Dense)              (None, 15)                315       
_________________________________________________________________
dense_9 (Dense)              (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [44]:
display_score(score_train13, score_test13)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [45]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste13"]).decode("utf8"))

01_0.3013.json
03_0.3013.json
05_0.3313.json
06_0.3713.json
07_0.3913.json
08_0.5413.json
110_0.8713.json
144_0.9113.json
177_0.9113.json
197_0.9113.json
206_0.9313.json
212_0.9313.json
218_0.9613.json
219_0.9613.json
22_0.5413.json
237_0.9813.json
25_0.5713.json
26_0.5713.json
28_0.5913.json
306_1.0013.json
33_0.6113.json
36_0.6313.json
37_0.6513.json
38_0.6713.json
47_0.7213.json
53_0.7413.json
57_0.7613.json
61_0.7813.json
75_0.8013.json
77_0.8313.json
90_0.8513.json
97_0.8513.json



##### Época = 306 - Acc: 1.00

#### 2.2 Teste da Camada Oculta (Hidden Layer) =  Função de Ativação 'Softmax'

In [46]:
model22, arquivo22 = verific_load_or_create(20, 15, 7, 'relu', 'softmax', 'softmax', '22')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_19 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_20 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_21 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [47]:
history22, score_train22, score_test22 = history_model(model22, arquivo22, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '22')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 21ms/step - loss: 1.9344 - acc: 0.1087 - mean_squared_error: 0.1220 - val_loss: 1.9339 - val_acc: 0.1429 - val_mean_squared_error: 0.1220

Epoch 00001: acc improved from -inf to 0.10870, saving model to /home/willian/Keras_Litologia/model_save/Teste22/01_0.1122.json
Epoch 2/2500
46/46 [==============================] - 0s 400us/step - loss: 1.9085 - acc: 0.2174 - mean_squared_error: 0.1209 - val_loss: 1.9232 - val_acc: 0.2857 - val_mean_squared_error: 0.1215

Epoch 00002: acc improved from 0.10870 to 0.21739, saving model to /home/willian/Keras_Litologia/model_save/Teste22/02_0.2222.json
Epoch 3/2500
46/46 [==============================] - 0s 648us/step - loss: 1.8715 - acc: 0.3478 - mean_squared_error: 0.1194 - val_loss: 1.9132 - val_acc: 0.2857 - val_mean_squared_error: 0.1211

Epoch 00003: acc improved from 0.21739 to 0.34783, saving model to /home/willian/Keras_Litologia/model_save/


Epoch 00029: acc did not improve from 0.65217
Epoch 30/2500
46/46 [==============================] - 0s 987us/step - loss: 0.8153 - acc: 0.6739 - mean_squared_error: 0.0608 - val_loss: 1.1218 - val_acc: 0.5714 - val_mean_squared_error: 0.0769

Epoch 00030: acc improved from 0.65217 to 0.67391, saving model to /home/willian/Keras_Litologia/model_save/Teste22/30_0.6722.json
Epoch 31/2500
46/46 [==============================] - 0s 900us/step - loss: 0.8080 - acc: 0.6957 - mean_squared_error: 0.0605 - val_loss: 1.0185 - val_acc: 0.5714 - val_mean_squared_error: 0.0694

Epoch 00031: acc improved from 0.67391 to 0.69565, saving model to /home/willian/Keras_Litologia/model_save/Teste22/31_0.7022.json
Epoch 32/2500
46/46 [==============================] - 0s 546us/step - loss: 0.7797 - acc: 0.7391 - mean_squared_error: 0.0578 - val_loss: 0.9768 - val_acc: 0.5714 - val_mean_squared_error: 0.0678

Epoch 00032: acc improved from 0.69565 to 0.73913, saving model to /home/willian/Keras_Litologia/

46/46 [==============================] - 0s 564us/step - loss: 0.4711 - acc: 0.7826 - mean_squared_error: 0.0378 - val_loss: 0.5546 - val_acc: 0.7143 - val_mean_squared_error: 0.0501

Epoch 00061: acc did not improve from 0.82609
Epoch 62/2500
46/46 [==============================] - 0s 838us/step - loss: 0.4971 - acc: 0.8043 - mean_squared_error: 0.0405 - val_loss: 0.4698 - val_acc: 0.7143 - val_mean_squared_error: 0.0399

Epoch 00062: acc did not improve from 0.82609
Epoch 63/2500
46/46 [==============================] - 0s 858us/step - loss: 0.4896 - acc: 0.7826 - mean_squared_error: 0.0373 - val_loss: 0.4218 - val_acc: 0.8571 - val_mean_squared_error: 0.0312

Epoch 00063: acc did not improve from 0.82609
Epoch 64/2500
46/46 [==============================] - 0s 627us/step - loss: 0.5223 - acc: 0.7391 - mean_squared_error: 0.0423 - val_loss: 0.4194 - val_acc: 0.8571 - val_mean_squared_error: 0.0334

Epoch 00064: acc did not improve from 0.82609
Epoch 65/2500
46/46 [=================

46/46 [==============================] - 0s 503us/step - loss: 0.3738 - acc: 0.8913 - mean_squared_error: 0.0295 - val_loss: 0.3032 - val_acc: 0.8571 - val_mean_squared_error: 0.0246

Epoch 00094: acc did not improve from 0.89130
Epoch 95/2500
46/46 [==============================] - 0s 491us/step - loss: 0.3831 - acc: 0.8261 - mean_squared_error: 0.0308 - val_loss: 0.2829 - val_acc: 0.8571 - val_mean_squared_error: 0.0225

Epoch 00095: acc did not improve from 0.89130
Epoch 96/2500
46/46 [==============================] - 0s 506us/step - loss: 0.3834 - acc: 0.8696 - mean_squared_error: 0.0306 - val_loss: 0.2064 - val_acc: 1.0000 - val_mean_squared_error: 0.0123

Epoch 00096: acc did not improve from 0.89130
Epoch 97/2500
46/46 [==============================] - 0s 715us/step - loss: 0.3717 - acc: 0.8913 - mean_squared_error: 0.0289 - val_loss: 0.2558 - val_acc: 0.8571 - val_mean_squared_error: 0.0185

Epoch 00097: acc did not improve from 0.89130
Epoch 98/2500
46/46 [=================


Epoch 00127: acc improved from 0.89130 to 0.89130, saving model to /home/willian/Keras_Litologia/model_save/Teste22/127_0.8922.json
Epoch 128/2500
46/46 [==============================] - 0s 955us/step - loss: 0.3378 - acc: 0.8696 - mean_squared_error: 0.0272 - val_loss: 0.2189 - val_acc: 0.8571 - val_mean_squared_error: 0.0154

Epoch 00128: acc did not improve from 0.89130
Epoch 129/2500
46/46 [==============================] - 0s 796us/step - loss: 0.3154 - acc: 0.9348 - mean_squared_error: 0.0236 - val_loss: 0.2459 - val_acc: 0.8571 - val_mean_squared_error: 0.0203

Epoch 00129: acc improved from 0.89130 to 0.93478, saving model to /home/willian/Keras_Litologia/model_save/Teste22/129_0.9322.json
Epoch 130/2500
46/46 [==============================] - 0s 517us/step - loss: 0.3326 - acc: 0.8261 - mean_squared_error: 0.0267 - val_loss: 0.2392 - val_acc: 0.8571 - val_mean_squared_error: 0.0189

Epoch 00130: acc did not improve from 0.93478
Epoch 131/2500
46/46 [========================

...

46/46 [==============================] - 0s 611us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 1.9717e-06 - val_loss: 2.5473 - val_acc: 0.7143 - val_mean_squared_error: 0.0643

Epoch 02345: acc did not improve from 1.00000
Epoch 2346/2500
46/46 [==============================] - 0s 530us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 1.9553e-06 - val_loss: 2.5472 - val_acc: 0.7143 - val_mean_squared_error: 0.0642

Epoch 02346: acc did not improve from 1.00000
Epoch 2347/2500
46/46 [==============================] - 0s 497us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.0706e-06 - val_loss: 2.5501 - val_acc: 0.7143 - val_mean_squared_error: 0.0648

Epoch 02347: acc did not improve from 1.00000
Epoch 2348/2500
46/46 [==============================] - 0s 521us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 2.0094e-06 - val_loss: 2.5497 - val_acc: 0.7143 - val_mean_squared_error: 0.0647

Epoch 02348: acc did not improve from 1.00000
Epoch 2349/2500


46/46 [==============================] - 0s 560us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.1415e-06 - val_loss: 2.5540 - val_acc: 0.7143 - val_mean_squared_error: 0.0657

Epoch 02378: acc did not improve from 1.00000
Epoch 2379/2500
46/46 [==============================] - 0s 466us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 1.9220e-06 - val_loss: 2.5517 - val_acc: 0.7143 - val_mean_squared_error: 0.0654

Epoch 02379: acc did not improve from 1.00000
Epoch 2380/2500
46/46 [==============================] - 0s 495us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 1.8666e-06 - val_loss: 2.5509 - val_acc: 0.7143 - val_mean_squared_error: 0.0648

Epoch 02380: acc did not improve from 1.00000
Epoch 2381/2500
46/46 [==============================] - 0s 602us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.2103e-06 - val_loss: 2.5416 - val_acc: 0.7143 - val_mean_squared_error: 0.0634

Epoch 02381: acc did not improve from 1.00000
Epoch 2382/2500



Epoch 02410: acc did not improve from 1.00000
Epoch 2411/2500
46/46 [==============================] - 0s 473us/step - loss: 9.9142e-04 - acc: 1.0000 - mean_squared_error: 1.8033e-06 - val_loss: 2.5458 - val_acc: 0.7143 - val_mean_squared_error: 0.0648

Epoch 02411: acc did not improve from 1.00000
Epoch 2412/2500
46/46 [==============================] - 0s 515us/step - loss: 9.6798e-04 - acc: 1.0000 - mean_squared_error: 1.6810e-06 - val_loss: 2.5479 - val_acc: 0.7143 - val_mean_squared_error: 0.0649

Epoch 02412: acc did not improve from 1.00000
Epoch 2413/2500
46/46 [==============================] - 0s 1ms/step - loss: 9.6430e-04 - acc: 1.0000 - mean_squared_error: 1.6662e-06 - val_loss: 2.5490 - val_acc: 0.7143 - val_mean_squared_error: 0.0649

Epoch 02413: acc did not improve from 1.00000
Epoch 2414/2500
46/46 [==============================] - 0s 918us/step - loss: 9.7834e-04 - acc: 1.0000 - mean_squared_error: 1.7393e-06 - val_loss: 2.5485 - val_acc: 0.7143 - val_mean_squared_

46/46 [==============================] - 0s 436us/step - loss: 9.8490e-04 - acc: 1.0000 - mean_squared_error: 1.7991e-06 - val_loss: 2.5529 - val_acc: 0.7143 - val_mean_squared_error: 0.0651

Epoch 02443: acc did not improve from 1.00000
Epoch 2444/2500
46/46 [==============================] - 0s 459us/step - loss: 9.7502e-04 - acc: 1.0000 - mean_squared_error: 1.7911e-06 - val_loss: 2.5442 - val_acc: 0.7143 - val_mean_squared_error: 0.0639

Epoch 02444: acc did not improve from 1.00000
Epoch 2445/2500
46/46 [==============================] - 0s 607us/step - loss: 9.9362e-04 - acc: 1.0000 - mean_squared_error: 1.9999e-06 - val_loss: 2.5431 - val_acc: 0.7143 - val_mean_squared_error: 0.0637

Epoch 02445: acc did not improve from 1.00000
Epoch 2446/2500
46/46 [==============================] - 0s 529us/step - loss: 9.7701e-04 - acc: 1.0000 - mean_squared_error: 1.8612e-06 - val_loss: 2.5487 - val_acc: 0.7143 - val_mean_squared_error: 0.0644

Epoch 02446: acc did not improve from 1.00000


46/46 [==============================] - 0s 520us/step - loss: 9.2985e-04 - acc: 1.0000 - mean_squared_error: 1.5822e-06 - val_loss: 2.5474 - val_acc: 0.7143 - val_mean_squared_error: 0.0642

Epoch 02475: acc did not improve from 1.00000
Epoch 2476/2500
46/46 [==============================] - 0s 478us/step - loss: 9.4089e-04 - acc: 1.0000 - mean_squared_error: 1.6650e-06 - val_loss: 2.5492 - val_acc: 0.7143 - val_mean_squared_error: 0.0642

Epoch 02476: acc did not improve from 1.00000
Epoch 2477/2500
46/46 [==============================] - 0s 827us/step - loss: 9.3963e-04 - acc: 1.0000 - mean_squared_error: 1.6495e-06 - val_loss: 2.5502 - val_acc: 0.7143 - val_mean_squared_error: 0.0645

Epoch 02477: acc did not improve from 1.00000
Epoch 2478/2500
46/46 [==============================] - 0s 548us/step - loss: 9.4982e-04 - acc: 1.0000 - mean_squared_error: 1.6942e-06 - val_loss: 2.5486 - val_acc: 0.7143 - val_mean_squared_error: 0.0646

Epoch 02478: acc did not improve from 1.00000


In [49]:
display_score(score_train22, score_test22)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 28.57%
 Test Accuracy: 0.7142857313156128


In [50]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste22"]).decode("utf8"))

01_0.0922.json
01_0.1122.json
02_0.2022.json
02_0.2222.json
03_0.2022.json
03_0.3522.json
04_0.4122.json
05_0.2422.json
07_0.4122.json
08_0.3022.json
08_0.4122.json
09_0.4122.json
10_0.4322.json
104_0.8722.json
11_0.4322.json
113_0.8922.json
12_0.4622.json
127_0.8922.json
129_0.9322.json
13_0.4822.json
138_0.9322.json
14_0.6122.json
145_0.8922.json
15_0.4622.json
15_0.6122.json
155_0.9822.json
158_0.9122.json
16_0.4822.json
166_0.9122.json
17_0.5022.json
171_0.9322.json
18_0.5722.json
190_0.9622.json
19_0.5922.json
19_0.6322.json
20_0.6322.json
225_0.9622.json
23_0.6522.json
23_0.6722.json
240_0.9822.json
25_0.6522.json
257_1.0022.json
281_1.0022.json
30_0.6722.json
31_0.7022.json
32_0.7422.json
35_0.8022.json
40_0.7422.json
42_0.7422.json
43_0.7622.json
43_0.8322.json
48_0.7622.json
48_0.8322.json
52_0.8022.json
59_0.8322.json
71_0.8522.json
71_0.8922.json



##### Época = 257 - Acc: 1.00 

#### 2.3 Teste da Camada Oculta (Hidden Layer) =  Função de Ativação 'Tangente' 

In [52]:
model23, arquivo23 = verific_load_or_create(20, 15, 7, 'relu', 'tanh', 'softmax', '23')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_22 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_23 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_24 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [53]:
history23, score_train23, score_test23 = history_model(model23, arquivo23, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '23')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 20ms/step - loss: 1.9328 - acc: 0.1957 - mean_squared_error: 0.1219 - val_loss: 1.9290 - val_acc: 0.1429 - val_mean_squared_error: 0.1217

Epoch 00001: acc improved from -inf to 0.19565, saving model to /home/willian/Keras_Litologia/model_save/Teste23/01_0.2023.json
Epoch 2/2500
46/46 [==============================] - 0s 386us/step - loss: 1.8975 - acc: 0.1957 - mean_squared_error: 0.1204 - val_loss: 1.9017 - val_acc: 0.1429 - val_mean_squared_error: 0.1205

Epoch 00002: acc improved from 0.19565 to 0.19565, saving model to /home/willian/Keras_Litologia/model_save/Teste23/02_0.2023.json
Epoch 3/2500
46/46 [==============================] - 0s 854us/step - loss: 1.8606 - acc: 0.1957 - mean_squared_error: 0.1187 - val_loss: 1.8794 - val_acc: 0.1429 - val_mean_squared_error: 0.1194

Epoch 00003: acc did not improve from 0.19565
Epoch 4/2500
46/46 [==============================] - 0s 519us

46/46 [==============================] - 0s 654us/step - loss: 0.8593 - acc: 0.6522 - mean_squared_error: 0.0661 - val_loss: 1.2140 - val_acc: 0.5714 - val_mean_squared_error: 0.0863

Epoch 00029: acc did not improve from 0.65217
Epoch 30/2500
46/46 [==============================] - 0s 461us/step - loss: 0.8216 - acc: 0.6522 - mean_squared_error: 0.0633 - val_loss: 1.1698 - val_acc: 0.5714 - val_mean_squared_error: 0.0836

Epoch 00030: acc did not improve from 0.65217
Epoch 31/2500
46/46 [==============================] - 0s 513us/step - loss: 0.8203 - acc: 0.6522 - mean_squared_error: 0.0638 - val_loss: 1.1235 - val_acc: 0.5714 - val_mean_squared_error: 0.0809

Epoch 00031: acc did not improve from 0.65217
Epoch 32/2500
46/46 [==============================] - 0s 704us/step - loss: 0.7948 - acc: 0.6522 - mean_squared_error: 0.0622 - val_loss: 1.1210 - val_acc: 0.5714 - val_mean_squared_error: 0.0829

Epoch 00032: acc did not improve from 0.65217
Epoch 33/2500
46/46 [=================

46/46 [==============================] - 0s 584us/step - loss: 0.5000 - acc: 0.7609 - mean_squared_error: 0.0401 - val_loss: 0.5190 - val_acc: 0.7143 - val_mean_squared_error: 0.0468

Epoch 00060: acc did not improve from 0.80435
Epoch 61/2500
46/46 [==============================] - 0s 793us/step - loss: 0.5052 - acc: 0.7391 - mean_squared_error: 0.0419 - val_loss: 0.5326 - val_acc: 0.8571 - val_mean_squared_error: 0.0483

Epoch 00061: acc did not improve from 0.80435
Epoch 62/2500
46/46 [==============================] - 0s 351us/step - loss: 0.4902 - acc: 0.8043 - mean_squared_error: 0.0399 - val_loss: 0.5297 - val_acc: 0.5714 - val_mean_squared_error: 0.0497

Epoch 00062: acc did not improve from 0.80435
Epoch 63/2500
46/46 [==============================] - 0s 630us/step - loss: 0.4707 - acc: 0.8261 - mean_squared_error: 0.0377 - val_loss: 0.4794 - val_acc: 0.7143 - val_mean_squared_error: 0.0416

Epoch 00063: acc improved from 0.80435 to 0.82609, saving model to /home/willian/Ker

46/46 [==============================] - 0s 588us/step - loss: 0.3823 - acc: 0.8043 - mean_squared_error: 0.0317 - val_loss: 0.2540 - val_acc: 1.0000 - val_mean_squared_error: 0.0181

Epoch 00093: acc did not improve from 0.82609
Epoch 94/2500
46/46 [==============================] - 0s 429us/step - loss: 0.3874 - acc: 0.7609 - mean_squared_error: 0.0324 - val_loss: 0.2551 - val_acc: 1.0000 - val_mean_squared_error: 0.0178

Epoch 00094: acc did not improve from 0.82609
Epoch 95/2500
46/46 [==============================] - 0s 575us/step - loss: 0.3767 - acc: 0.8043 - mean_squared_error: 0.0314 - val_loss: 0.2676 - val_acc: 0.8571 - val_mean_squared_error: 0.0196

Epoch 00095: acc did not improve from 0.82609
Epoch 96/2500
46/46 [==============================] - 0s 680us/step - loss: 0.3781 - acc: 0.8261 - mean_squared_error: 0.0317 - val_loss: 0.2810 - val_acc: 0.8571 - val_mean_squared_error: 0.0218

Epoch 00096: acc did not improve from 0.82609
Epoch 97/2500
46/46 [=================

46/46 [==============================] - 0s 410us/step - loss: 0.3464 - acc: 0.8043 - mean_squared_error: 0.0292 - val_loss: 0.2171 - val_acc: 0.8571 - val_mean_squared_error: 0.0161

Epoch 00126: acc did not improve from 0.86957
Epoch 127/2500
46/46 [==============================] - 0s 371us/step - loss: 0.3631 - acc: 0.8043 - mean_squared_error: 0.0317 - val_loss: 0.2504 - val_acc: 0.8571 - val_mean_squared_error: 0.0214

Epoch 00127: acc did not improve from 0.86957
Epoch 128/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.3451 - acc: 0.8261 - mean_squared_error: 0.0294 - val_loss: 0.1931 - val_acc: 1.0000 - val_mean_squared_error: 0.0125

Epoch 00128: acc did not improve from 0.86957
Epoch 129/2500
46/46 [==============================] - 0s 353us/step - loss: 0.3398 - acc: 0.8478 - mean_squared_error: 0.0287 - val_loss: 0.1816 - val_acc: 1.0000 - val_mean_squared_error: 0.0117

Epoch 00129: acc did not improve from 0.86957
Epoch 130/2500
46/46 [===============

...


Epoch 02340: acc did not improve from 1.00000
Epoch 2341/2500
46/46 [==============================] - 0s 684us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 2.4140e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02341: acc did not improve from 1.00000
Epoch 2342/2500
46/46 [==============================] - 0s 565us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 2.1740e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 577us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 2.0573e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02343: acc did not improve from 1.00000
Epoch 2344/2500
46/46 [==============================] - 0s 581us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.4071e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407


46/46 [==============================] - 0s 606us/step - loss: 0.0010 - acc: 1.0000 - mean_squared_error: 2.1080e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02373: acc did not improve from 1.00000
Epoch 2374/2500
46/46 [==============================] - 0s 519us/step - loss: 9.9718e-04 - acc: 1.0000 - mean_squared_error: 2.1004e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 728us/step - loss: 9.6829e-04 - acc: 1.0000 - mean_squared_error: 1.9117e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 471us/step - loss: 9.6772e-04 - acc: 1.0000 - mean_squared_error: 1.9805e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02376: acc did not improve from 1.00000
Epoc

46/46 [==============================] - 0s 501us/step - loss: 9.1846e-04 - acc: 1.0000 - mean_squared_error: 1.7291e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02405: acc did not improve from 1.00000
Epoch 2406/2500
46/46 [==============================] - 0s 566us/step - loss: 9.5824e-04 - acc: 1.0000 - mean_squared_error: 1.9797e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02406: acc did not improve from 1.00000
Epoch 2407/2500
46/46 [==============================] - 0s 508us/step - loss: 9.8341e-04 - acc: 1.0000 - mean_squared_error: 2.1244e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 576us/step - loss: 9.7160e-04 - acc: 1.0000 - mean_squared_error: 2.0073e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02408: acc did not improve from 1.00000


46/46 [==============================] - 0s 502us/step - loss: 9.2968e-04 - acc: 1.0000 - mean_squared_error: 1.8103e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02437: acc did not improve from 1.00000
Epoch 2438/2500
46/46 [==============================] - 0s 650us/step - loss: 9.2698e-04 - acc: 1.0000 - mean_squared_error: 1.7695e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02438: acc did not improve from 1.00000
Epoch 2439/2500
46/46 [==============================] - 0s 480us/step - loss: 9.4129e-04 - acc: 1.0000 - mean_squared_error: 1.8087e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02439: acc did not improve from 1.00000
Epoch 2440/2500
46/46 [==============================] - 0s 817us/step - loss: 9.4862e-04 - acc: 1.0000 - mean_squared_error: 1.8953e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02440: acc did not improve from 1.00000


46/46 [==============================] - 0s 371us/step - loss: 8.9292e-04 - acc: 1.0000 - mean_squared_error: 1.6804e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0407

Epoch 02469: acc did not improve from 1.00000
Epoch 2470/2500
46/46 [==============================] - 0s 470us/step - loss: 8.9176e-04 - acc: 1.0000 - mean_squared_error: 1.6305e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02470: acc did not improve from 1.00000
Epoch 2471/2500
46/46 [==============================] - 0s 466us/step - loss: 9.3071e-04 - acc: 1.0000 - mean_squared_error: 1.9308e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02471: acc did not improve from 1.00000
Epoch 2472/2500
46/46 [==============================] - 0s 679us/step - loss: 9.1886e-04 - acc: 1.0000 - mean_squared_error: 1.8464e-06 - val_loss: 2.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02472: acc did not improve from 1.00000


In [54]:
display_score(score_train23, score_test23)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [55]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste23"]).decode("utf8"))

01_0.2023.json
02_0.2023.json
04_0.2223.json
05_0.3023.json
06_0.3323.json
07_0.3723.json
08_0.4123.json
09_0.4323.json
10_0.5023.json
111_0.8723.json
12_0.5423.json
13_0.5723.json
14_0.5923.json
150_0.8923.json
166_0.9123.json
18_0.6123.json
182_0.9123.json
193_0.9323.json
198_0.9323.json
20_0.6523.json
238_0.9623.json
260_0.9623.json
26_0.6523.json
268_0.9623.json
283_0.9823.json
314_0.9823.json
34_0.6723.json
35_0.7223.json
36_0.7423.json
41_0.7623.json
43_0.7823.json
468_1.0023.json
47_0.8023.json
54_0.8023.json
63_0.8323.json



##### Época = 468 - Acc: 1.00 

#### 2.4 Teste da Camada Oculta (Hidden Layer) =  Função de Ativação 'Sigmoid'

In [60]:
model24, arquivo24 = verific_load_or_create(20, 15, 7, 'relu', 'sigmoid', 'softmax', '24')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_28 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_29 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_30 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [61]:
history24, score_train24, score_test24 = history_model(model24, arquivo24, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '24')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 28ms/step - loss: 1.9542 - acc: 0.0870 - mean_squared_error: 0.1228 - val_loss: 1.9478 - val_acc: 0.1429 - val_mean_squared_error: 0.1225

Epoch 00001: acc improved from -inf to 0.08696, saving model to /home/willian/Keras_Litologia/model_save/Teste24/01_0.0924.json
Epoch 2/2500
46/46 [==============================] - 0s 373us/step - loss: 1.9376 - acc: 0.3043 - mean_squared_error: 0.1221 - val_loss: 1.9407 - val_acc: 0.2857 - val_mean_squared_error: 0.1222

Epoch 00002: acc improved from 0.08696 to 0.30435, saving model to /home/willian/Keras_Litologia/model_save/Teste24/02_0.3024.json
Epoch 3/2500
46/46 [==============================] - 0s 978us/step - loss: 1.9221 - acc: 0.3478 - mean_squared_error: 0.1215 - val_loss: 1.9306 - val_acc: 0.2857 - val_mean_squared_error: 0.1218

Epoch 00003: acc improved from 0.30435 to 0.34783, saving model to /home/willian/Keras_Litologia/model_save/

46/46 [==============================] - 0s 420us/step - loss: 0.8841 - acc: 0.5870 - mean_squared_error: 0.0665 - val_loss: 1.1164 - val_acc: 0.7143 - val_mean_squared_error: 0.0794

Epoch 00030: acc did not improve from 0.60870
Epoch 31/2500
46/46 [==============================] - 0s 585us/step - loss: 0.8576 - acc: 0.6087 - mean_squared_error: 0.0650 - val_loss: 1.0972 - val_acc: 0.7143 - val_mean_squared_error: 0.0791

Epoch 00031: acc did not improve from 0.60870
Epoch 32/2500
46/46 [==============================] - 0s 742us/step - loss: 0.8383 - acc: 0.6304 - mean_squared_error: 0.0641 - val_loss: 1.0496 - val_acc: 0.7143 - val_mean_squared_error: 0.0755

Epoch 00032: acc improved from 0.60870 to 0.63043, saving model to /home/willian/Keras_Litologia/model_save/Teste24/32_0.6324.json
Epoch 33/2500
46/46 [==============================] - 0s 949us/step - loss: 0.8394 - acc: 0.6087 - mean_squared_error: 0.0645 - val_loss: 1.0640 - val_acc: 0.5714 - val_mean_squared_error: 0.0776


46/46 [==============================] - 0s 993us/step - loss: 0.5271 - acc: 0.7391 - mean_squared_error: 0.0433 - val_loss: 0.4321 - val_acc: 0.8571 - val_mean_squared_error: 0.0348

Epoch 00062: acc did not improve from 0.78261
Epoch 63/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.5015 - acc: 0.7826 - mean_squared_error: 0.0394 - val_loss: 0.3583 - val_acc: 0.8571 - val_mean_squared_error: 0.0273

Epoch 00063: acc did not improve from 0.78261
Epoch 64/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.5214 - acc: 0.8478 - mean_squared_error: 0.0416 - val_loss: 0.3742 - val_acc: 0.8571 - val_mean_squared_error: 0.0284

Epoch 00064: acc improved from 0.78261 to 0.84783, saving model to /home/willian/Keras_Litologia/model_save/Teste24/64_0.8524.json
Epoch 65/2500
46/46 [==============================] - 0s 622us/step - loss: 0.4904 - acc: 0.8696 - mean_squared_error: 0.0383 - val_loss: 0.4151 - val_acc: 0.8571 - val_mean_squared_error: 0.0334

Epo


Epoch 00094: acc did not improve from 0.89130
Epoch 95/2500
46/46 [==============================] - 0s 642us/step - loss: 0.3856 - acc: 0.8043 - mean_squared_error: 0.0318 - val_loss: 0.3299 - val_acc: 0.8571 - val_mean_squared_error: 0.0251

Epoch 00095: acc did not improve from 0.89130
Epoch 96/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.3975 - acc: 0.8696 - mean_squared_error: 0.0336 - val_loss: 0.2893 - val_acc: 0.8571 - val_mean_squared_error: 0.0217

Epoch 00096: acc did not improve from 0.89130
Epoch 97/2500
46/46 [==============================] - 0s 789us/step - loss: 0.4068 - acc: 0.8696 - mean_squared_error: 0.0322 - val_loss: 0.2656 - val_acc: 0.8571 - val_mean_squared_error: 0.0214

Epoch 00097: acc did not improve from 0.89130
Epoch 98/2500
46/46 [==============================] - 0s 843us/step - loss: 0.4059 - acc: 0.8043 - mean_squared_error: 0.0344 - val_loss: 0.2946 - val_acc: 0.8571 - val_mean_squared_error: 0.0225

Epoch 00098: acc did not 

46/46 [==============================] - 0s 837us/step - loss: 0.3305 - acc: 0.8913 - mean_squared_error: 0.0273 - val_loss: 0.3192 - val_acc: 0.8571 - val_mean_squared_error: 0.0285

Epoch 00128: acc did not improve from 0.89130
Epoch 129/2500
46/46 [==============================] - 0s 982us/step - loss: 0.3596 - acc: 0.8261 - mean_squared_error: 0.0306 - val_loss: 0.2878 - val_acc: 0.8571 - val_mean_squared_error: 0.0255

Epoch 00129: acc did not improve from 0.89130
Epoch 130/2500
46/46 [==============================] - 0s 862us/step - loss: 0.3399 - acc: 0.8478 - mean_squared_error: 0.0283 - val_loss: 0.2674 - val_acc: 0.8571 - val_mean_squared_error: 0.0206

Epoch 00130: acc did not improve from 0.89130
Epoch 131/2500
46/46 [==============================] - 0s 945us/step - loss: 0.4416 - acc: 0.7826 - mean_squared_error: 0.0374 - val_loss: 0.3656 - val_acc: 0.8571 - val_mean_squared_error: 0.0270

Epoch 00131: acc did not improve from 0.89130
Epoch 132/2500
46/46 [=============

...

46/46 [==============================] - 0s 486us/step - loss: 0.0023 - acc: 1.0000 - mean_squared_error: 9.9654e-06 - val_loss: 1.7543 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02348: acc did not improve from 1.00000
Epoch 2349/2500
46/46 [==============================] - 0s 434us/step - loss: 0.0024 - acc: 1.0000 - mean_squared_error: 1.1120e-05 - val_loss: 1.7690 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02349: acc did not improve from 1.00000
Epoch 2350/2500
46/46 [==============================] - 0s 604us/step - loss: 0.0024 - acc: 1.0000 - mean_squared_error: 1.1035e-05 - val_loss: 1.7553 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02350: acc did not improve from 1.00000
Epoch 2351/2500
46/46 [==============================] - 0s 529us/step - loss: 0.0023 - acc: 1.0000 - mean_squared_error: 9.7181e-06 - val_loss: 1.7771 - val_acc: 0.8571 - val_mean_squared_error: 0.0416

Epoch 02351: acc did not improve from 1.00000
Epoch 2352/2500


46/46 [==============================] - 0s 543us/step - loss: 0.0022 - acc: 1.0000 - mean_squared_error: 8.5801e-06 - val_loss: 1.7744 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02381: acc did not improve from 1.00000
Epoch 2382/2500
46/46 [==============================] - 0s 613us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.1745e-06 - val_loss: 1.7873 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02382: acc did not improve from 1.00000
Epoch 2383/2500
46/46 [==============================] - 0s 524us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.5270e-06 - val_loss: 1.7855 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02383: acc did not improve from 1.00000
Epoch 2384/2500
46/46 [==============================] - 0s 558us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.4358e-06 - val_loss: 1.7821 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02384: acc did not improve from 1.00000
Epoch 2385/2500


46/46 [==============================] - 0s 637us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.3119e-06 - val_loss: 1.8230 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02414: acc did not improve from 1.00000
Epoch 2415/2500
46/46 [==============================] - 0s 681us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.8201e-06 - val_loss: 1.8280 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02415: acc did not improve from 1.00000
Epoch 2416/2500
46/46 [==============================] - 0s 876us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 8.5432e-06 - val_loss: 1.8048 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02416: acc did not improve from 1.00000
Epoch 2417/2500
46/46 [==============================] - 0s 438us/step - loss: 0.0021 - acc: 1.0000 - mean_squared_error: 7.9591e-06 - val_loss: 1.8041 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02417: acc did not improve from 1.00000
Epoch 2418/2500


46/46 [==============================] - 0s 601us/step - loss: 0.0020 - acc: 1.0000 - mean_squared_error: 7.1786e-06 - val_loss: 1.8203 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02447: acc did not improve from 1.00000
Epoch 2448/2500
46/46 [==============================] - 0s 644us/step - loss: 0.0019 - acc: 1.0000 - mean_squared_error: 6.7612e-06 - val_loss: 1.8238 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02448: acc did not improve from 1.00000
Epoch 2449/2500
46/46 [==============================] - 0s 518us/step - loss: 0.0020 - acc: 1.0000 - mean_squared_error: 7.3195e-06 - val_loss: 1.8235 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02449: acc did not improve from 1.00000
Epoch 2450/2500
46/46 [==============================] - 0s 601us/step - loss: 0.0019 - acc: 1.0000 - mean_squared_error: 6.6318e-06 - val_loss: 1.8310 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02450: acc did not improve from 1.00000
Epoch 2451/2500


46/46 [==============================] - 0s 571us/step - loss: 0.0018 - acc: 1.0000 - mean_squared_error: 6.5049e-06 - val_loss: 1.8618 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02480: acc did not improve from 1.00000
Epoch 2481/2500
46/46 [==============================] - 0s 739us/step - loss: 0.0019 - acc: 1.0000 - mean_squared_error: 6.5857e-06 - val_loss: 1.8579 - val_acc: 0.8571 - val_mean_squared_error: 0.0415

Epoch 02481: acc did not improve from 1.00000
Epoch 2482/2500
46/46 [==============================] - 0s 584us/step - loss: 0.0019 - acc: 1.0000 - mean_squared_error: 6.4402e-06 - val_loss: 1.8563 - val_acc: 0.8571 - val_mean_squared_error: 0.0414

Epoch 02482: acc did not improve from 1.00000
Epoch 2483/2500
46/46 [==============================] - 0s 458us/step - loss: 0.0019 - acc: 1.0000 - mean_squared_error: 6.5562e-06 - val_loss: 1.8608 - val_acc: 0.8571 - val_mean_squared_error: 0.0414

Epoch 02483: acc did not improve from 1.00000
Epoch 2484/2500


In [63]:
display_score(score_train24, score_test24)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [64]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste24"]).decode("utf8"))

01_0.0924.json
02_0.3024.json
03_0.3524.json
04_0.5024.json
111_0.8924.json
146_0.9324.json
15_0.5424.json
155_0.9324.json
16_0.5724.json
18_0.5724.json
218_0.9624.json
23_0.5924.json
234_0.9824.json
24_0.6124.json
245_0.9824.json
26_0.6124.json
27_0.6124.json
29_0.6124.json
303_1.0024.json
32_0.6324.json
35_0.7024.json
36_0.7224.json
43_0.7624.json
59_0.7824.json
64_0.8524.json
65_0.8724.json
75_0.8924.json



##### Época = 303 - Acc: 1.00 

### 3 - Camada Saída (Outpur-Layers) : função de ativação

##### Obs: O modelo que apresentou o melhor resultado foi o 2.4, com a função de ativação da camada oculta sigmoid,  todos os teste foram realizados usando a função Relu na camada na cama de input e a softmax na camada de saída, como também uma rede configurada com os seguintes parâmetros: neurônio input 20, neurônio hidden 15 e neurônio output 7 . Os próximos teste serão realizados alterando a função de ativação da camada de saída.

#### 3.1 Teste da Camada de Saída (Output Layer) =  Função de Ativação 'Sigmoid' ( 2.4 do teste anterior)

In [66]:
model24.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_28 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_29 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_30 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [67]:
display_score(score_train24, score_test24)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [68]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste24"]).decode("utf8"))

01_0.0924.json
02_0.3024.json
03_0.3524.json
04_0.5024.json
111_0.8924.json
146_0.9324.json
15_0.5424.json
155_0.9324.json
16_0.5724.json
18_0.5724.json
218_0.9624.json
23_0.5924.json
234_0.9824.json
24_0.6124.json
245_0.9824.json
26_0.6124.json
27_0.6124.json
29_0.6124.json
303_1.0024.json
32_0.6324.json
35_0.7024.json
36_0.7224.json
43_0.7624.json
59_0.7824.json
64_0.8524.json
65_0.8724.json
75_0.8924.json



##### Época = 303 - Acc: 1.00 

#### 3.2 Teste da Camada de Saída (Output Layer) = Função de Ativação 'Sigmoid'

In [70]:
model32, arquivo32 = verific_load_or_create(20, 15, 7, 'relu', 'sigmoid', 'sigmoid', '32')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_31 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_32 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_33 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [71]:
history32, score_train32, score_test32 = history_model(model32, arquivo32, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '32')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 1s 28ms/step - loss: 1.9401 - acc: 0.1304 - mean_squared_error: 0.1222 - val_loss: 1.9444 - val_acc: 0.4286 - val_mean_squared_error: 0.1224

Epoch 00001: acc improved from -inf to 0.13043, saving model to /home/willian/Keras_Litologia/model_save/Teste32/01_0.1332.json
Epoch 2/2500
46/46 [==============================] - 0s 407us/step - loss: 1.9169 - acc: 0.2609 - mean_squared_error: 0.1213 - val_loss: 1.9541 - val_acc: 0.2857 - val_mean_squared_error: 0.1227

Epoch 00002: acc improved from 0.13043 to 0.26087, saving model to /home/willian/Keras_Litologia/model_save/Teste32/02_0.2632.json
Epoch 3/2500
46/46 [==============================] - 0s 586us/step - loss: 1.8689 - acc: 0.2826 - mean_squared_error: 0.1194 - val_loss: 1.9489 - val_acc: 0.1429 - val_mean_squared_error: 0.1221

Epoch 00003: acc improved from 0.26087 to 0.28261, saving model to /home/willian/Keras_Litologia/model_save/


Epoch 00030: acc did not improve from 0.67391
Epoch 31/2500
46/46 [==============================] - 0s 730us/step - loss: 0.8338 - acc: 0.6304 - mean_squared_error: 0.0674 - val_loss: 1.0403 - val_acc: 0.5714 - val_mean_squared_error: 0.0824

Epoch 00031: acc did not improve from 0.67391
Epoch 32/2500
46/46 [==============================] - 0s 637us/step - loss: 0.8012 - acc: 0.6522 - mean_squared_error: 0.0643 - val_loss: 1.0030 - val_acc: 0.4286 - val_mean_squared_error: 0.0769

Epoch 00032: acc did not improve from 0.67391
Epoch 33/2500
46/46 [==============================] - 0s 800us/step - loss: 0.8012 - acc: 0.6304 - mean_squared_error: 0.0647 - val_loss: 0.9995 - val_acc: 0.5714 - val_mean_squared_error: 0.0758

Epoch 00033: acc did not improve from 0.67391
Epoch 34/2500
46/46 [==============================] - 0s 582us/step - loss: 0.7788 - acc: 0.6522 - mean_squared_error: 0.0630 - val_loss: 0.9697 - val_acc: 0.4286 - val_mean_squared_error: 0.0780

Epoch 00034: acc did no


Epoch 00062: acc did not improve from 0.80435
Epoch 63/2500
46/46 [==============================] - 0s 541us/step - loss: 0.5130 - acc: 0.7826 - mean_squared_error: 0.0422 - val_loss: 0.4465 - val_acc: 0.8571 - val_mean_squared_error: 0.0372

Epoch 00063: acc did not improve from 0.80435
Epoch 64/2500
46/46 [==============================] - 0s 583us/step - loss: 0.4940 - acc: 0.8261 - mean_squared_error: 0.0386 - val_loss: 0.3884 - val_acc: 0.8571 - val_mean_squared_error: 0.0316

Epoch 00064: acc improved from 0.80435 to 0.82609, saving model to /home/willian/Keras_Litologia/model_save/Teste32/64_0.8332.json
Epoch 65/2500
46/46 [==============================] - 0s 808us/step - loss: 0.4918 - acc: 0.7391 - mean_squared_error: 0.0394 - val_loss: 0.4334 - val_acc: 0.7143 - val_mean_squared_error: 0.0375

Epoch 00065: acc did not improve from 0.82609
Epoch 66/2500
46/46 [==============================] - 0s 705us/step - loss: 0.4929 - acc: 0.7826 - mean_squared_error: 0.0403 - val_los

46/46 [==============================] - 0s 567us/step - loss: 0.3964 - acc: 0.8043 - mean_squared_error: 0.0325 - val_loss: 0.3267 - val_acc: 0.8571 - val_mean_squared_error: 0.0280

Epoch 00095: acc did not improve from 0.84783
Epoch 96/2500
46/46 [==============================] - 0s 622us/step - loss: 0.3830 - acc: 0.8043 - mean_squared_error: 0.0314 - val_loss: 0.3188 - val_acc: 1.0000 - val_mean_squared_error: 0.0268

Epoch 00096: acc did not improve from 0.84783
Epoch 97/2500
46/46 [==============================] - 0s 541us/step - loss: 0.4051 - acc: 0.7609 - mean_squared_error: 0.0341 - val_loss: 0.3175 - val_acc: 0.8571 - val_mean_squared_error: 0.0270

Epoch 00097: acc did not improve from 0.84783
Epoch 98/2500
46/46 [==============================] - 0s 716us/step - loss: 0.3802 - acc: 0.7826 - mean_squared_error: 0.0319 - val_loss: 0.3125 - val_acc: 0.8571 - val_mean_squared_error: 0.0265

Epoch 00098: acc did not improve from 0.84783
Epoch 99/2500
46/46 [=================

46/46 [==============================] - 0s 660us/step - loss: 0.3384 - acc: 0.8261 - mean_squared_error: 0.0280 - val_loss: 0.2366 - val_acc: 0.8571 - val_mean_squared_error: 0.0187

Epoch 00128: acc did not improve from 0.86957
Epoch 129/2500
46/46 [==============================] - 0s 618us/step - loss: 0.3434 - acc: 0.8043 - mean_squared_error: 0.0287 - val_loss: 0.2318 - val_acc: 0.8571 - val_mean_squared_error: 0.0187

Epoch 00129: acc did not improve from 0.86957
Epoch 130/2500
46/46 [==============================] - 0s 541us/step - loss: 0.3431 - acc: 0.8043 - mean_squared_error: 0.0293 - val_loss: 0.2355 - val_acc: 0.8571 - val_mean_squared_error: 0.0182

Epoch 00130: acc did not improve from 0.86957
Epoch 131/2500
46/46 [==============================] - 0s 562us/step - loss: 0.3339 - acc: 0.8478 - mean_squared_error: 0.0278 - val_loss: 0.2600 - val_acc: 0.8571 - val_mean_squared_error: 0.0217

Epoch 00131: acc did not improve from 0.86957
Epoch 132/2500
46/46 [=============

...


Epoch 02339: acc did not improve from 1.00000
Epoch 2340/2500
46/46 [==============================] - 0s 482us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.9891e-06 - val_loss: 2.2454 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02340: acc did not improve from 1.00000
Epoch 2341/2500
46/46 [==============================] - 0s 435us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.9066e-06 - val_loss: 2.2288 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02341: acc did not improve from 1.00000
Epoch 2342/2500
46/46 [==============================] - 0s 533us/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 4.2832e-06 - val_loss: 2.2467 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 988us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 3.4121e-06 - val_loss: 2.2340 - val_acc: 0.8571 - val_mean_squared_error: 0.0408



Epoch 02372: acc did not improve from 1.00000
Epoch 2373/2500
46/46 [==============================] - 0s 497us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 2.9214e-06 - val_loss: 2.2513 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02373: acc did not improve from 1.00000
Epoch 2374/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.0641e-06 - val_loss: 2.2463 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 530us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.3443e-06 - val_loss: 2.2484 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 993us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.0407e-06 - val_loss: 2.2536 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

E


Epoch 02405: acc did not improve from 1.00000
Epoch 2406/2500
46/46 [==============================] - 0s 827us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6322e-06 - val_loss: 2.2776 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02406: acc did not improve from 1.00000
Epoch 2407/2500
46/46 [==============================] - 0s 768us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.5830e-06 - val_loss: 2.2936 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 880us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.2885e-06 - val_loss: 2.2702 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02408: acc did not improve from 1.00000
Epoch 2409/2500
46/46 [==============================] - 0s 877us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.8300e-06 - val_loss: 2.2650 - val_acc: 0.8571 - val_mean_squared_error: 0.0408



Epoch 02438: acc did not improve from 1.00000
Epoch 2439/2500
46/46 [==============================] - 0s 662us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6726e-06 - val_loss: 2.2819 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02439: acc did not improve from 1.00000
Epoch 2440/2500
46/46 [==============================] - 0s 453us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 2.9306e-06 - val_loss: 2.2766 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02440: acc did not improve from 1.00000
Epoch 2441/2500
46/46 [==============================] - 0s 500us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.7805e-06 - val_loss: 2.2876 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02441: acc did not improve from 1.00000
Epoch 2442/2500
46/46 [==============================] - 0s 594us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.0207e-06 - val_loss: 2.2845 - val_acc: 0.8571 - val_mean_squared_error: 0.0408



Epoch 02471: acc did not improve from 1.00000
Epoch 2472/2500
46/46 [==============================] - 0s 560us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.1987e-06 - val_loss: 2.2800 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02472: acc did not improve from 1.00000
Epoch 2473/2500
46/46 [==============================] - 0s 499us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.8096e-06 - val_loss: 2.2979 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02473: acc did not improve from 1.00000
Epoch 2474/2500
46/46 [==============================] - 0s 617us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.4200e-06 - val_loss: 2.3027 - val_acc: 0.8571 - val_mean_squared_error: 0.0408

Epoch 02474: acc did not improve from 1.00000
Epoch 2475/2500
46/46 [==============================] - 0s 593us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.2944e-06 - val_loss: 2.3027 - val_acc: 0.8571 - val_mean_squared_error: 0.0408


In [72]:
display_score(score_train32, score_test32)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [73]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste32"]).decode("utf8"))

01_0.1332.json
02_0.2632.json
03_0.2832.json
04_0.5232.json
08_0.5432.json
09_0.5732.json
10_0.5732.json
11_0.5932.json
120_0.8732.json
14_0.5932.json
145_0.8932.json
146_0.9132.json
173_0.9132.json
178_0.9132.json
193_0.9332.json
20_0.6132.json
204_0.9332.json
229_0.9632.json
232_0.9832.json
27_0.6732.json
302_0.9832.json
410_1.0032.json
45_0.7032.json
46_0.7232.json
48_0.7432.json
49_0.7832.json
54_0.8032.json
64_0.8332.json
78_0.8532.json
92_0.8532.json



##### Época = 410 - Acc: 1.00 

#### 3.3 Teste da Camada de Saída (Output Layer) = Função de Ativação 'Tangente'

In [75]:
model33, arquivo33 = verific_load_or_create(20, 15, 7, 'relu', 'sigmoid', 'tanh', '33')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_34 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_35 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_36 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [76]:
history33, score_train33, score_test33 = history_model(model33, arquivo33, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '33')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 2s 35ms/step - loss: 1.9348 - acc: 0.1304 - mean_squared_error: 0.1220 - val_loss: 1.9426 - val_acc: 0.1429 - val_mean_squared_error: 0.1223

Epoch 00001: acc improved from -inf to 0.13043, saving model to /home/willian/Keras_Litologia/model_save/Teste33/01_0.1333.json
Epoch 2/2500
46/46 [==============================] - 0s 506us/step - loss: 1.9157 - acc: 0.1522 - mean_squared_error: 0.1213 - val_loss: 1.9410 - val_acc: 0.1429 - val_mean_squared_error: 0.1223

Epoch 00002: acc improved from 0.13043 to 0.15217, saving model to /home/willian/Keras_Litologia/model_save/Teste33/02_0.1533.json
Epoch 3/2500
46/46 [==============================] - 0s 603us/step - loss: 1.8937 - acc: 0.1522 - mean_squared_error: 0.1204 - val_loss: 1.9410 - val_acc: 0.1429 - val_mean_squared_error: 0.1223

Epoch 00003: acc did not improve from 0.15217
Epoch 4/2500
46/46 [==============================] - 0s 817us

Epoch 00029: acc did not improve from 0.67391
Epoch 30/2500
46/46 [==============================] - 0s 652us/step - loss: 0.9220 - acc: 0.6739 - mean_squared_error: 0.0702 - val_loss: 1.1985 - val_acc: 0.5714 - val_mean_squared_error: 0.0873

Epoch 00030: acc improved from 0.67391 to 0.67391, saving model to /home/willian/Keras_Litologia/model_save/Teste33/30_0.6733.json
Epoch 31/2500
46/46 [==============================] - 0s 950us/step - loss: 0.8968 - acc: 0.6522 - mean_squared_error: 0.0694 - val_loss: 1.1889 - val_acc: 0.5714 - val_mean_squared_error: 0.0877

Epoch 00031: acc did not improve from 0.67391
Epoch 32/2500
46/46 [==============================] - 0s 711us/step - loss: 0.8585 - acc: 0.6522 - mean_squared_error: 0.0663 - val_loss: 1.1594 - val_acc: 0.5714 - val_mean_squared_error: 0.0844

Epoch 00032: acc did not improve from 0.67391
Epoch 33/2500
46/46 [==============================] - 0s 644us/step - loss: 0.8537 - acc: 0.6304 - mean_squared_error: 0.0662 - val_loss

46/46 [==============================] - 0s 465us/step - loss: 0.5056 - acc: 0.7391 - mean_squared_error: 0.0399 - val_loss: 0.5301 - val_acc: 0.7143 - val_mean_squared_error: 0.0412

Epoch 00062: acc did not improve from 0.76087
Epoch 63/2500
46/46 [==============================] - 0s 461us/step - loss: 0.5747 - acc: 0.7391 - mean_squared_error: 0.0467 - val_loss: 0.4756 - val_acc: 1.0000 - val_mean_squared_error: 0.0357

Epoch 00063: acc did not improve from 0.76087
Epoch 64/2500
46/46 [==============================] - 0s 513us/step - loss: 0.5007 - acc: 0.8043 - mean_squared_error: 0.0374 - val_loss: 0.5701 - val_acc: 0.7143 - val_mean_squared_error: 0.0494

Epoch 00064: acc improved from 0.76087 to 0.80435, saving model to /home/willian/Keras_Litologia/model_save/Teste33/64_0.8033.json
Epoch 65/2500
46/46 [==============================] - 0s 980us/step - loss: 0.5344 - acc: 0.7826 - mean_squared_error: 0.0441 - val_loss: 0.6019 - val_acc: 0.7143 - val_mean_squared_error: 0.0527


46/46 [==============================] - 0s 606us/step - loss: 0.4172 - acc: 0.8261 - mean_squared_error: 0.0335 - val_loss: 0.3394 - val_acc: 0.8571 - val_mean_squared_error: 0.0251

Epoch 00094: acc did not improve from 0.84783
Epoch 95/2500
46/46 [==============================] - 0s 614us/step - loss: 0.3898 - acc: 0.8043 - mean_squared_error: 0.0323 - val_loss: 0.3029 - val_acc: 0.8571 - val_mean_squared_error: 0.0222

Epoch 00095: acc did not improve from 0.84783
Epoch 96/2500
46/46 [==============================] - 0s 396us/step - loss: 0.3916 - acc: 0.8696 - mean_squared_error: 0.0308 - val_loss: 0.2921 - val_acc: 1.0000 - val_mean_squared_error: 0.0203

Epoch 00096: acc improved from 0.84783 to 0.86957, saving model to /home/willian/Keras_Litologia/model_save/Teste33/96_0.8733.json
Epoch 97/2500
46/46 [==============================] - 0s 546us/step - loss: 0.4154 - acc: 0.8043 - mean_squared_error: 0.0341 - val_loss: 0.2988 - val_acc: 0.8571 - val_mean_squared_error: 0.0202



Epoch 00125: acc did not improve from 0.91304
Epoch 126/2500
46/46 [==============================] - 0s 468us/step - loss: 0.3509 - acc: 0.8261 - mean_squared_error: 0.0294 - val_loss: 0.2481 - val_acc: 0.8571 - val_mean_squared_error: 0.0199

Epoch 00126: acc did not improve from 0.91304
Epoch 127/2500
46/46 [==============================] - 0s 525us/step - loss: 0.3177 - acc: 0.8478 - mean_squared_error: 0.0266 - val_loss: 0.2594 - val_acc: 0.8571 - val_mean_squared_error: 0.0193

Epoch 00127: acc did not improve from 0.91304
Epoch 128/2500
46/46 [==============================] - 0s 535us/step - loss: 0.3353 - acc: 0.8261 - mean_squared_error: 0.0282 - val_loss: 0.2197 - val_acc: 0.8571 - val_mean_squared_error: 0.0161

Epoch 00128: acc did not improve from 0.91304
Epoch 129/2500
46/46 [==============================] - 0s 474us/step - loss: 0.3783 - acc: 0.7826 - mean_squared_error: 0.0327 - val_loss: 0.2543 - val_acc: 0.8571 - val_mean_squared_error: 0.0187

Epoch 00129: acc di

...

46/46 [==============================] - 0s 444us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.7535e-06 - val_loss: 2.3888 - val_acc: 0.8571 - val_mean_squared_error: 0.0489

Epoch 02344: acc did not improve from 1.00000
Epoch 2345/2500
46/46 [==============================] - 0s 605us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.6446e-06 - val_loss: 2.3922 - val_acc: 0.8571 - val_mean_squared_error: 0.0493

Epoch 02345: acc did not improve from 1.00000
Epoch 2346/2500
46/46 [==============================] - 0s 818us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.6064e-06 - val_loss: 2.3959 - val_acc: 0.8571 - val_mean_squared_error: 0.0498

Epoch 02346: acc did not improve from 1.00000
Epoch 2347/2500
46/46 [==============================] - 0s 759us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.8756e-06 - val_loss: 2.3950 - val_acc: 0.8571 - val_mean_squared_error: 0.0497

Epoch 02347: acc did not improve from 1.00000
Epoch 2348/2500


46/46 [==============================] - 0s 567us/step - loss: 0.0015 - acc: 1.0000 - mean_squared_error: 5.5830e-06 - val_loss: 2.3930 - val_acc: 0.8571 - val_mean_squared_error: 0.0495

Epoch 02377: acc did not improve from 1.00000
Epoch 2378/2500
46/46 [==============================] - 0s 468us/step - loss: 0.0014 - acc: 1.0000 - mean_squared_error: 4.4371e-06 - val_loss: 2.3948 - val_acc: 0.8571 - val_mean_squared_error: 0.0497

Epoch 02378: acc did not improve from 1.00000
Epoch 2379/2500
46/46 [==============================] - 0s 562us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 4.1498e-06 - val_loss: 2.3944 - val_acc: 0.8571 - val_mean_squared_error: 0.0497

Epoch 02379: acc did not improve from 1.00000
Epoch 2380/2500
46/46 [==============================] - 0s 643us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 4.0018e-06 - val_loss: 2.3932 - val_acc: 0.8571 - val_mean_squared_error: 0.0494

Epoch 02380: acc did not improve from 1.00000
Epoch 2381/2500


46/46 [==============================] - 0s 462us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.9539e-06 - val_loss: 2.3936 - val_acc: 0.8571 - val_mean_squared_error: 0.0495

Epoch 02410: acc did not improve from 1.00000
Epoch 2411/2500
46/46 [==============================] - 0s 613us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.7222e-06 - val_loss: 2.3962 - val_acc: 0.8571 - val_mean_squared_error: 0.0499

Epoch 02411: acc did not improve from 1.00000
Epoch 2412/2500
46/46 [==============================] - 0s 532us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.9411e-06 - val_loss: 2.3958 - val_acc: 0.8571 - val_mean_squared_error: 0.0499

Epoch 02412: acc did not improve from 1.00000
Epoch 2413/2500
46/46 [==============================] - 0s 617us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.8359e-06 - val_loss: 2.3951 - val_acc: 0.8571 - val_mean_squared_error: 0.0498

Epoch 02413: acc did not improve from 1.00000
Epoch 2414/2500


46/46 [==============================] - 0s 399us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.7946e-06 - val_loss: 2.3974 - val_acc: 0.8571 - val_mean_squared_error: 0.0501

Epoch 02443: acc did not improve from 1.00000
Epoch 2444/2500
46/46 [==============================] - 0s 848us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 4.0409e-06 - val_loss: 2.3987 - val_acc: 0.8571 - val_mean_squared_error: 0.0503

Epoch 02444: acc did not improve from 1.00000
Epoch 2445/2500
46/46 [==============================] - 0s 581us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.9639e-06 - val_loss: 2.3944 - val_acc: 0.8571 - val_mean_squared_error: 0.0497

Epoch 02445: acc did not improve from 1.00000
Epoch 2446/2500
46/46 [==============================] - 0s 725us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.6245e-06 - val_loss: 2.3918 - val_acc: 0.8571 - val_mean_squared_error: 0.0493

Epoch 02446: acc did not improve from 1.00000
Epoch 2447/2500


46/46 [==============================] - 0s 495us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 3.5878e-06 - val_loss: 2.3981 - val_acc: 0.8571 - val_mean_squared_error: 0.0502

Epoch 02476: acc did not improve from 1.00000
Epoch 2477/2500
46/46 [==============================] - 0s 474us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 4.1026e-06 - val_loss: 2.3943 - val_acc: 0.8571 - val_mean_squared_error: 0.0496

Epoch 02477: acc did not improve from 1.00000
Epoch 2478/2500
46/46 [==============================] - 0s 506us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.7465e-06 - val_loss: 2.3938 - val_acc: 0.8571 - val_mean_squared_error: 0.0495

Epoch 02478: acc did not improve from 1.00000
Epoch 2479/2500
46/46 [==============================] - 0s 553us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.6688e-06 - val_loss: 2.4004 - val_acc: 0.8571 - val_mean_squared_error: 0.0506

Epoch 02479: acc did not improve from 1.00000
Epoch 2480/2500


In [77]:
display_score(score_train33, score_test33)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [78]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste33"]).decode("utf8"))

01_0.1333.json
02_0.1533.json
04_0.1733.json
05_0.3033.json
06_0.3533.json
09_0.3733.json
10_0.4633.json
102_0.8733.json
108_0.8933.json
11_0.5433.json
117_0.8933.json
119_0.9133.json
12_0.5733.json
133_0.9133.json
134_0.9333.json
18_0.5733.json
195_0.9633.json
22_0.5733.json
223_0.9833.json
26_0.6133.json
27_0.6733.json
299_0.9833.json
30_0.6733.json
308_1.0033.json
42_0.7233.json
49_0.7233.json
50_0.7633.json
64_0.8033.json
70_0.8333.json
73_0.8333.json
78_0.8533.json
96_0.8733.json



##### Época = 308 - Acc: 1.00 

#### 3.4 Teste da Camada de Saída (Output Layer) = Função de Ativação 'Relu'

In [79]:
model34, arquivo34 = verific_load_or_create(20, 15, 7, 'relu', 'sigmoid', 'relu', '34')

Created to model.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_37 (Dense)             (None, 20)                420       
_________________________________________________________________
dense_38 (Dense)             (None, 15)                315       
_________________________________________________________________
dense_39 (Dense)             (None, 7)                 112       
Total params: 847
Trainable params: 847
Non-trainable params: 0
_________________________________________________________________


In [80]:
history34, score_train34, score_test34 = history_model(model34, arquivo34, x_train, y_train, x_test, y_test, epoch, batch_s, path_file_models, '34')

Train on 46 samples, validate on 7 samples
Epoch 1/2500
46/46 [==============================] - 2s 33ms/step - loss: 1.9393 - acc: 0.1087 - mean_squared_error: 0.1222 - val_loss: 1.9384 - val_acc: 0.2857 - val_mean_squared_error: 0.1221

Epoch 00001: acc improved from -inf to 0.10870, saving model to /home/willian/Keras_Litologia/model_save/Teste34/01_0.1134.json
Epoch 2/2500
46/46 [==============================] - 0s 377us/step - loss: 1.9231 - acc: 0.2391 - mean_squared_error: 0.1215 - val_loss: 1.9332 - val_acc: 0.1429 - val_mean_squared_error: 0.1220

Epoch 00002: acc improved from 0.10870 to 0.23913, saving model to /home/willian/Keras_Litologia/model_save/Teste34/02_0.2434.json
Epoch 3/2500
46/46 [==============================] - 0s 653us/step - loss: 1.9056 - acc: 0.2609 - mean_squared_error: 0.1209 - val_loss: 1.9327 - val_acc: 0.1429 - val_mean_squared_error: 0.1219

Epoch 00003: acc improved from 0.23913 to 0.26087, saving model to /home/willian/Keras_Litologia/model_save/


Epoch 00028: acc did not improve from 0.69565
Epoch 29/2500
46/46 [==============================] - 0s 496us/step - loss: 0.9385 - acc: 0.6739 - mean_squared_error: 0.0652 - val_loss: 1.2351 - val_acc: 0.5714 - val_mean_squared_error: 0.0749

Epoch 00029: acc did not improve from 0.69565
Epoch 30/2500
46/46 [==============================] - 0s 627us/step - loss: 0.9012 - acc: 0.6739 - mean_squared_error: 0.0626 - val_loss: 1.2137 - val_acc: 0.5714 - val_mean_squared_error: 0.0739

Epoch 00030: acc did not improve from 0.69565
Epoch 31/2500
46/46 [==============================] - 0s 500us/step - loss: 0.8719 - acc: 0.6739 - mean_squared_error: 0.0608 - val_loss: 1.1609 - val_acc: 0.5714 - val_mean_squared_error: 0.0714

Epoch 00031: acc did not improve from 0.69565
Epoch 32/2500
46/46 [==============================] - 0s 916us/step - loss: 0.8451 - acc: 0.6957 - mean_squared_error: 0.0596 - val_loss: 1.1140 - val_acc: 0.5714 - val_mean_squared_error: 0.0686

Epoch 00032: acc improv

46/46 [==============================] - 0s 1ms/step - loss: 0.4873 - acc: 0.7826 - mean_squared_error: 0.0385 - val_loss: 0.4294 - val_acc: 0.7143 - val_mean_squared_error: 0.0327

Epoch 00060: acc did not improve from 0.82609
Epoch 61/2500
46/46 [==============================] - 0s 321us/step - loss: 0.4563 - acc: 0.8261 - mean_squared_error: 0.0347 - val_loss: 0.4047 - val_acc: 1.0000 - val_mean_squared_error: 0.0298

Epoch 00061: acc did not improve from 0.82609
Epoch 62/2500
46/46 [==============================] - 0s 326us/step - loss: 0.4613 - acc: 0.8043 - mean_squared_error: 0.0363 - val_loss: 0.4095 - val_acc: 1.0000 - val_mean_squared_error: 0.0313

Epoch 00062: acc did not improve from 0.82609
Epoch 63/2500
46/46 [==============================] - 0s 371us/step - loss: 0.4382 - acc: 0.8043 - mean_squared_error: 0.0340 - val_loss: 0.4170 - val_acc: 0.8571 - val_mean_squared_error: 0.0340

Epoch 00063: acc did not improve from 0.82609
Epoch 64/2500
46/46 [===================


Epoch 00092: acc did not improve from 0.84783
Epoch 93/2500
46/46 [==============================] - 0s 341us/step - loss: 0.3937 - acc: 0.8043 - mean_squared_error: 0.0334 - val_loss: 0.2443 - val_acc: 1.0000 - val_mean_squared_error: 0.0162

Epoch 00093: acc did not improve from 0.84783
Epoch 94/2500
46/46 [==============================] - 0s 342us/step - loss: 0.3794 - acc: 0.7826 - mean_squared_error: 0.0306 - val_loss: 0.2621 - val_acc: 0.8571 - val_mean_squared_error: 0.0201

Epoch 00094: acc did not improve from 0.84783
Epoch 95/2500
46/46 [==============================] - 0s 341us/step - loss: 0.3701 - acc: 0.8261 - mean_squared_error: 0.0301 - val_loss: 0.2461 - val_acc: 1.0000 - val_mean_squared_error: 0.0162

Epoch 00095: acc did not improve from 0.84783
Epoch 96/2500
46/46 [==============================] - 0s 344us/step - loss: 0.4000 - acc: 0.8043 - mean_squared_error: 0.0334 - val_loss: 0.2680 - val_acc: 1.0000 - val_mean_squared_error: 0.0186

Epoch 00096: acc did no


Epoch 00125: acc did not improve from 0.89130
Epoch 126/2500
46/46 [==============================] - 0s 574us/step - loss: 0.3112 - acc: 0.8696 - mean_squared_error: 0.0258 - val_loss: 0.1878 - val_acc: 0.8571 - val_mean_squared_error: 0.0129

Epoch 00126: acc did not improve from 0.89130
Epoch 127/2500
46/46 [==============================] - 0s 1ms/step - loss: 0.3251 - acc: 0.8261 - mean_squared_error: 0.0269 - val_loss: 0.1782 - val_acc: 1.0000 - val_mean_squared_error: 0.0115

Epoch 00127: acc did not improve from 0.89130
Epoch 128/2500
46/46 [==============================] - 0s 429us/step - loss: 0.3232 - acc: 0.8478 - mean_squared_error: 0.0264 - val_loss: 0.1949 - val_acc: 0.8571 - val_mean_squared_error: 0.0134

Epoch 00128: acc did not improve from 0.89130
Epoch 129/2500
46/46 [==============================] - 0s 457us/step - loss: 0.3592 - acc: 0.8478 - mean_squared_error: 0.0317 - val_loss: 0.2649 - val_acc: 0.8571 - val_mean_squared_error: 0.0226

Epoch 00129: acc did 

...


Epoch 02341: acc did not improve from 1.00000
Epoch 2342/2500
46/46 [==============================] - 0s 830us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.8460e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0327

Epoch 02342: acc did not improve from 1.00000
Epoch 2343/2500
46/46 [==============================] - 0s 568us/step - loss: 0.0013 - acc: 1.0000 - mean_squared_error: 3.0881e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0328

Epoch 02343: acc did not improve from 1.00000
Epoch 2344/2500
46/46 [==============================] - 0s 551us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6633e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0325

Epoch 02344: acc did not improve from 1.00000
Epoch 2345/2500
46/46 [==============================] - 0s 808us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.7290e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0321



Epoch 02374: acc did not improve from 1.00000
Epoch 2375/2500
46/46 [==============================] - 0s 898us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6293e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0318

Epoch 02375: acc did not improve from 1.00000
Epoch 2376/2500
46/46 [==============================] - 0s 516us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.5785e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0315

Epoch 02376: acc did not improve from 1.00000
Epoch 2377/2500
46/46 [==============================] - 0s 964us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6417e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0318

Epoch 02377: acc did not improve from 1.00000
Epoch 2378/2500
46/46 [==============================] - 0s 870us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6238e-06 - val_loss: 2.3039 - val_acc: 0.8571 - val_mean_squared_error: 0.0321



Epoch 02407: acc did not improve from 1.00000
Epoch 2408/2500
46/46 [==============================] - 0s 551us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.4954e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0326

Epoch 02408: acc did not improve from 1.00000
Epoch 2409/2500
46/46 [==============================] - 0s 546us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.4010e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0321

Epoch 02409: acc did not improve from 1.00000
Epoch 2410/2500
46/46 [==============================] - 0s 746us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.3630e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0320

Epoch 02410: acc did not improve from 1.00000
Epoch 2411/2500
46/46 [==============================] - 0s 670us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.4324e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0319



Epoch 02440: acc did not improve from 1.00000
Epoch 2441/2500
46/46 [==============================] - 0s 833us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.6484e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0318

Epoch 02441: acc did not improve from 1.00000
Epoch 2442/2500
46/46 [==============================] - 0s 405us/step - loss: 0.0012 - acc: 1.0000 - mean_squared_error: 2.5957e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0324

Epoch 02442: acc did not improve from 1.00000
Epoch 2443/2500
46/46 [==============================] - 0s 696us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.5195e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0323

Epoch 02443: acc did not improve from 1.00000
Epoch 2444/2500
46/46 [==============================] - 0s 651us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.2272e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0321



Epoch 02473: acc did not improve from 1.00000
Epoch 2474/2500
46/46 [==============================] - 0s 679us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.3646e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0324

Epoch 02474: acc did not improve from 1.00000
Epoch 2475/2500
46/46 [==============================] - 0s 528us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.2539e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0322

Epoch 02475: acc did not improve from 1.00000
Epoch 2476/2500
46/46 [==============================] - 0s 658us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.2192e-06 - val_loss: 2.3037 - val_acc: 0.8571 - val_mean_squared_error: 0.0318

Epoch 02476: acc did not improve from 1.00000
Epoch 2477/2500
46/46 [==============================] - 0s 648us/step - loss: 0.0011 - acc: 1.0000 - mean_squared_error: 2.2956e-06 - val_loss: 2.3038 - val_acc: 0.8571 - val_mean_squared_error: 0.0318


In [81]:
display_score(score_train34, score_test34)

 Baseline Error Train: 0.00%
 Train Accuracy: 1.0
 Baseline Error Test: 14.29%
 Test Accuracy: 0.8571428656578064


In [82]:
print(check_output(["ls", "/home/willian/Keras_Litologia/model_save/Teste34"]).decode("utf8"))

01_0.1134.json
02_0.2434.json
03_0.2634.json
05_0.2634.json
06_0.2834.json
07_0.3734.json
08_0.4134.json
10_0.4834.json
101_0.8734.json
11_0.5234.json
120_0.8934.json
13_0.5234.json
132_0.8934.json
133_0.9134.json
15_0.5434.json
151_0.9334.json
16_0.5434.json
161_0.9634.json
18_0.6134.json
187_0.9834.json
19_0.6334.json
20_0.6334.json
23_0.6734.json
24_0.7034.json
316_1.0034.json
32_0.7034.json
33_0.7634.json
39_0.7634.json
43_0.7834.json
48_0.7834.json
58_0.8334.json
81_0.8334.json
84_0.8334.json
89_0.8534.json



##### Época = 316 - Acc: 1.00 